# Data Cleaning and Preprocessing

En este notebook haremos la limpieza y preprocesamiento de los datos en raw para trabajar sobre un dataset completo

Seguiremos los siguientes pasos:
 
- [1. Listar y cargar datos desde Kedro](#1.Listar-datos-del-catalog-disponibles)
- [2. EDA](#2.Exploratory-Data-Analysis-(EDA))
- [3. Igualar columnas en dataframes](#3.-Limpiamos-y-hacemos-iguales-las-columnas-para-todos-los-dataframes)
  - [3.1. Diccionarios para rename de columnas](#3.1.-Diccionarios-para-rename-de-columnas)
  - [3.2. Year por dataframe](#3.2.-Year-por-dataframe)
  - [3.3. Seleccionar y eliminar columnas o valores no deseados](#3.3.-Seleccionar-y-elimianr-columnas-o-valores-no-deseados)
- [4. Concat de los dataframes](#4.-Concat-de-los-dataframes)
- [5. Limpieza de datos](#5.-Limpieza-de-datos)
  - [5.1. Strip, Lower, remove punctuation marks and accents](#5.1.Strip,-Lower,-remove-punctuation-marks-and-accents)
  - [5.2 Valores NA](#5.2.-Valores-NA)
  - [5.3. Como tratar los valores faltantes (NaN)](#5.3.-Como-tratar-los-valores-faltantes-(NaN))
    - [5.3.1 Imputar valores](#5.3.1-Imputar-valores)
    - [5.3.2. Visitas y estancias](#5.3.2.-Visitas-y-estancias)
- [6. Replaces](#6.-Replaces:)
  - [6.1 Búsqueda de palabras](#6.1-Búsqueda-de-palabras)
  - [6.2 Diagnóstico](#6.2-Replace-diagnostico)
  - [6.3 Replace General y de la columna Hospital de procedencia](#6.3.-Replace-general-y-h_procedencia)
  - [6.4 Servicio de procedencia](#6.4.-Replace-s_procedencia)
  - [6.5 Motivo de ingreso](#6.5-Replace-motivo_ing)
  - [6.6 Motivo de alta](#6.6-Replace-motivo_alta)
  - [6.7 Médico](#6.7-Replace-medico)
  - [6.8 Sedación](#6.8-Replace-sedacion)
  - [6.9 Ayuntamiento](#6.9-Replace-ayuntamiento)
  - [6.10 Otros](#6.10-Replace-otros)
  - [6.11 Otros_1](#6.11-Replace-otros_1)
  - [6.12 Otros Complicaciones](#6.12-Replace-otros_complicaciones)
  - [6.13 Fecha de alta](#6.13-Fecha-alta)
  - [6.14 Ecog, Barthel, Evaluacion de ingreso y GDS Fast](#6.14.-Numéricos-[ps_ecog,-barthel,-gds_fast,-eva_ing])
- [7. Sedacion y medicamentos](#7.-Sedacion-si-tiene-o-no-tiene-y-tipos-de-medicamentos)
  
- [8. Notas](#8.-Notas)

In [55]:
# Importamos las librerias

import pandas as pd
import ydata_profiling as pp
import numpy as np
import matplotlib.pyplot as plt
from IPython import display
import string
import unidecode

pd.options.display.max_columns = None
pd.options.display.max_rows = None


## Bibliotecas documentación

### Pandas (pd)
Pandas es una biblioteca de manipulación y análisis de datos en Python. Proporciona estructuras de datos como DataFrames y Series para manejar datos tabulares de manera eficiente. Pandas es ampliamente utilizado para tareas como la limpieza de datos, transformaciones, agregaciones y visualizaciones básicas.

```python
pd.options.display.max_columns = None
pd.options.display.max_rows = None
```

Las líneas de código anteriores están configurando las opciones de visualización para que Pandas muestre todas las columnas y filas cuando se visualice un DataFrame.

### ydata_profiling (pp)
Esta biblioteca (antes llamada `pandas_profiling`) se usa generalmente para generar informes de perfil de datos. Estos informes ofrecen un análisis inicial y rápido para comprender la naturaleza de los datos, sus tipos, la existencia de valores faltantes, estadísticas descriptivas y más.

### NumPy (np)
NumPy es una biblioteca para el lenguaje de programación Python que da soporte para trabajar con arreglos y matrices, además de proporcionar una gran biblioteca de funciones matemáticas de alto nivel para operar con esos arreglos.

### Matplotlib (plt)
Matplotlib es una biblioteca de gráficos 2D en Python que produce figuras de calidad en una variedad de formatos impresos y entornos interactivos. Se utiliza para crear gráficos estáticos, interactivos y animados en Python.

### IPython display
La función `display` de IPython se utiliza para mostrar representaciones ricas de objetos. Se puede usar para mostrar gráficos, tablas HTML, entre otros. Es especialmente útil en Jupyter Notebooks.

### string
El módulo `string` contiene varias constantes, clases y funciones relacionadas con operaciones de cadena de texto. Se puede utilizar para la manipulación de texto y contiene, por ejemplo, constantes para todas las letras del alfabeto y símbolos de puntuación.

### unidecode
La biblioteca `unidecode` se utiliza para transliterar cualquier carácter Unicode (á, ü, ñ, etc.) a sus caracteres ASCII más cercanos. Esto es útil cuando se desea normalizar cadenas para hacerlas más simples para, por ejemplo, realizar comparaciones.

>En resumen, estas bibliotecas conjuntamente ofrecen un conjunto de herramientas poderosas para manipulación, análisis y visualización de datos, así como para la generación de informes descriptivos y la manipulación de cadenas de texto.

# 1.Listar y cargar datos del catalog disponibles

In [2]:
%load_ext kedro.ipython

[09/06/23 16:29:08] INFO     Resolved project path as: c:\Users\Pablo                               __init__.py:136
                             Villar\Desktop\CURSOS\KSchool\Máster en Data                                          
                             Science\TFM\nuevo_entorno_kedro\hado.                                                 
                             To set a different path, run '%reload_kedro <project_root>'                           

[09/06/23 16:29:09] WARNING  C:\Users\Pablo                                                         warnings.py:109
                             Villar\AppData\Local\Programs\Python\Python310\lib\importlib\__init__.                
                             py:126: DeprecationWarning: `kedro.extras.datasets` is deprecated and                 
                             will be removed in Kedro 0.19, install `kedro-datasets` instead by                    
                             running `pip install kedro-datasets`.                                                 
                               return _bootstrap._gcd_import(name[level:], package, level)                         
                                                                                                                   

[09/06/23 16:29:10] INFO     Kedro project hado                                                     __init__.py:105

                    INFO     Defined global variable 'context', 'session', 'catalog' and            __init__.py:106
                             'pipelines'                                                                           

[09/06/23 16:29:11] INFO     Registered line magic 'run_viz'                                        __init__.py:112

In [3]:
# Todos nuestros daframes empiezan con la palabra "hado"
catalog.list('hado')

['hado_22',
 'hado_21',
 'hado_20',
 'hado_19',
 'hado_18',
 'hado_17',
 'strip_lower_hado_17',
 'strip_lower_hado_18',
 'strip_lower_hado_19',
 'strip_lower_hado_20',
 'strip_lower_hado_21',
 'strip_lower_hado_22',
 'hado_concat',
 'hado_clean',
 'hado_clean_na',
 'hado_replaced_words',
 'hado_cleaned',
 'hado_cleaned_sedation',
 'hado_cleaned_medication',
 'hado_categorized',
 'hado_final',
 'hado_encoded']

In [4]:
df_22 = catalog.load('hado_22')
df_21 = catalog.load('hado_21')
df_20 = catalog.load('hado_20')
df_19 = catalog.load('hado_19')
df_18 = catalog.load('hado_18')
df_17 = catalog.load('hado_17')

                    INFO     Loading data from 'hado_22' (MongoDBDataSet)...                    data_catalog.py:345

                    INFO     Loading data from 'hado_21' (MongoDBDataSet)...                    data_catalog.py:345

                    INFO     Loading data from 'hado_20' (MongoDBDataSet)...                    data_catalog.py:345

                    INFO     Loading data from 'hado_19' (MongoDBDataSet)...                    data_catalog.py:345

                    INFO     Loading data from 'hado_18' (MongoDBDataSet)...                    data_catalog.py:345

                    INFO     Loading data from 'hado_17' (MongoDBDataSet)...                    data_catalog.py:345

# 2.Exploratory Data Analysis (EDA)

El Análisis Exploratorio de Datos (EDA, por sus siglas en inglés, Exploratory Data Analysis) es un enfoque inicial y fundamental en el análisis de datos. Sirve para resumir las principales características del conjunto de datos, a menudo visualmente, con el objetivo de comprender mejor la distribución, las tendencias y las relaciones entre las variables. El EDA se lleva a cabo antes de cualquier modelado estadístico o de aprendizaje automático más avanzado y es crucial para determinar cómo abordar problemas futuros en la analítica de datos.

>Es un paso que se realiza varias veces a lo largo del proyecto

Aquí hay algunas de las tareas más comunes que se realizan durante el EDA:

### Estadísticas Descriptivas
- Resumen estadístico (media, mediana, desviación estándar, etc.)
- Verificación de la existencia de valores nulos o perdidos
- Identificación de tipos de datos y dimensiones del conjunto de datos

### Visualización de Datos
- Gráficos de dispersión para observar relaciones entre variables
- Histogramas y gráficos de densidad para entender la distribución de las variables
- Diagramas de caja para identificar valores atípicos
- Mapas de calor para visualizar correlaciones entre variables

### Análisis de Relaciones y Patrones
- Identificación de correlaciones entre variables
- Identificación de variables categóricas y cómo se distribuyen en relación con otras variables
- Observar tendencias a lo largo del tiempo, si se dispone de datos temporales

### Preparación para el Modelado
- Identificación de variables que pueden ser útiles para la predicción
- Observación de posibles problemas que requieren transformaciones de datos, como la normalización
- Determinar si es necesario imputar o eliminar valores perdidos

El EDA es una etapa crucial en cualquier proyecto de ciencia de datos porque ofrece una oportunidad para entender mejor la calidad y la estructura del conjunto de datos antes de hacer supuestos o construir modelos.

Una forma rápida de hacer un EDA es a través de Pandas-Profiling

In [5]:
df_17.head()

Hospital Servicio  AP Otros                  Diagnostico  \
0  gil casares     upal  no    no                       ca orl   
1      clinico      ONC  no    no              Melanoma vulvar   
2      clinico      MIR  no    no              ca broncogenico   
3      clinico      DIG  no    no            cirrosis hepatica   
4      clinico      URG  no    no  neplasia de mama estadio IV   

                   Motivo Ing  paliativo Onc Paliativo No Onc Fiebre Disnea  \
0           contro d sintomas             si               si     no     no   
1           mal control dolor             si               no     no     no   
2           control evolutivo             si               si     no     si   
3  admininistacion octreotido             no               no     no     no   
4         control de sintomas             si               no     no     si   

  Dolor Delirium Astenia Anorexia Otros.1 P terminal Agonía PS/IK Barthel  \
0    si       no      si       si      no         si     no   4.0    30.0   
1    si       no      si       si      no         si     no   3-4      no   
2    no       no      no       no      no         no     no   3-4    40.0   
3    no       no      no       no      no         no     no   1.0    90.0   
4    si       no      no       no      no         si     no   4.0    30.0   

  GDS-FAST EVA ing Otros.2            Complicaciones  Nº estancias  \
0       no      no      no    reingreso en urgencias          21.0   
1       no      no      no  met. pulmonares y digest          24.0   
2       no      no      no                        no          14.0   
3       no      no      no                        no           1.0   
4       no     7.0      no                        no           2.0   

   Nº visitas SEDACIÓN        Mot. ALTA         Médico  unnamed.1  
0        10.0       no       reingreso          valdes        NaN  
1         8.0       no           exitus    galego feal        NaN  
2         6.0       no  fin de cuidados  lopez renedo.        NaN  
3         1.0       no  fin de cuidados  lopez renedo.        NaN  
4         1.0       no           exitus  lopez renedo.        NaN

In [6]:
df_17.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 587 entries, 0 to 586
Data columns (total 29 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   Hospital          586 non-null    object 
 1   Servicio          587 non-null    object 
 2   AP                586 non-null    object 
 3   Otros             587 non-null    object 
 4   Diagnostico       587 non-null    object 
 5   Motivo Ing        587 non-null    object 
 6    paliativo Onc    586 non-null    object 
 7   Paliativo No Onc  586 non-null    object 
 8   Fiebre            587 non-null    object 
 9   Disnea            586 non-null    object 
 10  Dolor             587 non-null    object 
 11  Delirium          587 non-null    object 
 12  Astenia           587 non-null    object 
 13  Anorexia          587 non-null    object 
 14  Otros.1           587 non-null    object 
 15  P terminal        587 non-null    object 
 16  Agonía            587 non-null    object 
 1

In [7]:
pp.ProfileReport(df_17, minimal=True, lazy=True)

[09/06/23 16:29:12] WARNING  c:\Users\Pablo Villar\Desktop\CURSOS\KSchool\Máster en Data            warnings.py:109
                             Science\TFM\nuevo_entorno_kedro\lib\site-packages\ydata_profiling\prof                
                             ile_report.py:489: DeprecationWarning: Importing display from                         
                             IPython.core.display is deprecated since IPython 7.14, please import                  
                             from IPython display                                                                  
                               from IPython.core.display import display                                            
                                                                                                                   

                    WARNING  c:\Users\Pablo Villar\Desktop\CURSOS\KSchool\Máster en Data            warnings.py:109
                             Science\TFM\nuevo_entorno_kedro\lib\site-packages\ydata_profiling\repo                
                             rt\presentation\flavours\widget\correlation_table.py:1:                               
                             DeprecationWarning: Importing display from IPython.core.display is                    
                             deprecated since IPython 7.14, please import from IPython display                     
                               from IPython.core.display import display                                            
                                                                                                                   

                    WARNING  c:\Users\Pablo Villar\Desktop\CURSOS\KSchool\Máster en Data            warnings.py:109
                             Science\TFM\nuevo_entorno_kedro\lib\site-packages\ydata_profiling\repo                
                             rt\presentation\flavours\widget\duplicate.py:1: DeprecationWarning:                   
                             Importing display from IPython.core.display is deprecated since                       
                             IPython 7.14, please import from IPython display                                      
                               from IPython.core.display import display                                            
                                                                                                                   

                    WARNING  c:\Users\Pablo Villar\Desktop\CURSOS\KSchool\Máster en Data            warnings.py:109
                             Science\TFM\nuevo_entorno_kedro\lib\site-packages\ydata_profiling\repo                
                             rt\presentation\flavours\widget\sample.py:1: DeprecationWarning:                      
                             Importing display from IPython.core.display is deprecated since                       
                             IPython 7.14, please import from IPython display                                      
                               from IPython.core.display import display                                            
                                                                                                                   

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# 3. Limpiamos y hacemos iguales las columnas para todos los dataframes 

Para hacer un único dataset que coja la información del resto de datasets cambio el nombre de todas las columnas con un diccionario.

* Las columnas y valores no son iguales en todos los datasets
* Para el año 2019 tenemos que cambiar las columnas otros para que no se solapen porque llevan espacios y se escriben igual
* Quitaremos los espacios de los nombres de las columnas y lo pasaremos a minúsculas

In [8]:
new_column_names = { ' Otros': 'otros', '   Otros': 'otros_1', '   Otros.1': 'otros_2'}

df_19 = df_19.rename(columns=new_column_names)

In [9]:
sorted(df_19.columns)

['    AP',
 '  Agonía',
 '  Dolor',
 '  Fiebre',
 '  PS/IK',
 ' Disnea',
 ' P. terminal ',
 ' pal Onc',
 'Anorexia',
 'Astenia',
 'Barthel',
 'Complicaciones',
 'Delirium',
 'Diagnostico',
 'EVA ing',
 'GDS-FAST',
 'Hospital',
 'Mot. ALTA',
 'Motivo Ing',
 'Médico',
 'Nº estancias',
 'Nº visitas',
 'Pal no Onc',
 'SEDACIÓN',
 'Servicio',
 'otros',
 'otros_1',
 'otros_2']

In [10]:
dfs = [df_17,df_18,df_19,df_20,df_21,df_22]

In [11]:
# Para visualizar que las columnas que tenemos estén sin espacios y en minúsculas además de visualizarlas
def columns_names_clean_sorted (dfs) -> list:
    for i, df in enumerate(dfs):
        i += 2017
        df.columns = df.columns.str.strip()
        df.columns = df.columns.str.lower()
        print("Columnas para los datos del año", i)
        print(f'\n{sorted(df.columns.to_list())}')
        print(f'\nEl número de columnas es {len(df.columns)}\n')
        print("="*80)
        
        
columns_names_clean_sorted(dfs)

Columnas para los datos del año 2017

['agonía', 'anorexia', 'ap', 'astenia', 'barthel', 'complicaciones', 'delirium', 'diagnostico', 'disnea', 'dolor', 'eva ing', 'fiebre', 'gds-fast', 'hospital', 'mot. alta', 'motivo ing', 'médico', 'nº estancias', 'nº visitas', 'otros', 'otros.1', 'otros.2', 'p terminal', 'paliativo no onc', 'paliativo onc', 'ps/ik', 'sedación', 'servicio', 'unnamed.1']

El número de columnas es 29

Columnas para los datos del año 2018

['agonía', 'anorexia', 'ap', 'astenia', 'barthel', 'complicaciones', 'delirium', 'diagnostico', 'disnea', 'dolor', 'eva ing', 'fiebre', 'gds-fast', 'hospital', 'mot. alta', 'motivo ing', 'médico', 'nº estancias', 'nº visitas', 'otros', 'otros.1', 'otros.2', 'p terminal', 'paliativo no onc', 'paliativo onc', 'ps/ik', 'sedación', 'servicio']

El número de columnas es 28

Columnas para los datos del año 2019

['agonía', 'anorexia', 'ap', 'astenia', 'barthel', 'complicaciones', 'delirium', 'diagnostico', 'disnea', 'dolor', 'eva ing', 'fi

## 3.1. Diccionarios para rename de columnas
Cambiamos los nombres de las columnas para estandarizar todos los datasets y poder concatenarlos

In [12]:
data_2017 = df_17.rename(columns={'hospital': 'h_procedencia',
                               'servicio': 's_procedencia',
                               'ap': 'ap',
                               'otros': 'otros',
                               'diagnostico': 'diagnostico',
                               'motivo ing': 'motivo_ing',
                               'paliativo onc': 'paliativo_onc_noc', 
                               'paliativo no onc': 'paliativo_no_onc_noc',
                               'fiebre': 'fiebre',
                               'disnea': 'disnea',
                               'dolor': 'dolor',
                               'delirium': 'delirium',
                               'astenia': 'astenia',
                               'anorexia': 'anorexia',                               
                               'otros.1': 'otros_1',
                               'agonía': 'agonia',
                               'p terminal': 'p_terminal',
                               'ps/ik': 'ps_ecog',
                               'barthel': 'barthel',
                               'gds-fast': 'gds_fast', 
                               'eva ing': 'eva_ing',
                               'otros.2': 'otros_2',
                               'complicaciones': 'otros_complicaciones',
                               'nº estancias': "n_estancias",
                               'nº visitas': "n_visitas",
                               'sedación': 'sedacion',
                               'mot. alta': 'motivo_alta', 
                               'médico': 'medico'})

data_2018 = df_18.rename(columns={'hospital': 'h_procedencia',
                               'servicio': 's_procedencia',
                               'ap': 'ap',
                               'otros': 'otros',
                               'diagnostico': 'diagnostico',
                               'motivo ing': 'motivo_ing',
                               'paliativo onc': 'paliativo_onc_noc', 
                               'paliativo no onc': 'paliativo_no_onc_noc',
                               'fiebre': 'fiebre',
                               'disnea': 'disnea',
                               'dolor': 'dolor',
                               'delirium': 'delirium',
                               'astenia': 'astenia',
                               'anorexia': 'anorexia',                               
                               'otros.1': 'otros_1',
                               'agonía': 'agonia',
                               'p terminal': 'p_terminal',
                               'ps/ik': 'ps_ecog',
                               'barthel': 'barthel',
                               'gds-fast': 'gds_fast', 
                               'eva ing': 'eva_ing',
                               'otros.2': 'otros_2',
                               'complicaciones': 'otros_complicaciones',
                               'nº estancias': "n_estancias",
                               'nº visitas': "n_visitas",
                               'sedación': 'sedacion',
                               'mot. alta': 'motivo_alta', 
                               'médico': 'medico'})
                               
data_2019 = df_19.rename(columns={'hospital': 'h_procedencia',
                               'servicio': 's_procedencia',
                               'ap': 'ap',
                               'otros': 'otros',
                               'diagnostico': 'diagnostico',
                               'motivo ing': 'motivo_ing',
                               'pal onc': 'paliativo_onc_noc', 
                               'pal no onc': 'paliativo_no_onc_noc',
                               'fiebre': 'fiebre',
                               'disnea': 'disnea',
                               'dolor': 'dolor',
                               'delirium': 'delirium',
                               'astenia': 'astenia',
                               'anorexia': 'anorexia',                               
                               'otros_1': 'otros_1', # Problema se repite otros en una colunmna ver si lo traga así
                               'agonía': 'agonia',
                               'p. terminal': 'p_terminal',
                               'ps/ik': 'ps_ecog',
                               'barthel': 'barthel',
                               'gds-fast': 'gds_fast', 
                               'eva ing': 'eva_ing',
                               'otros_2': 'otros_2',
                               'complicaciones': 'otros_complicaciones',
                               'nº estancias': "n_estancias",
                               'nº visitas': "n_visitas",
                               'sedación': 'sedacion',
                               'mot. alta': 'motivo_alta', 
                               'médico': 'medico'})
                               
data_2020 = df_20.rename(columns={'h proced': 'h_procedencia', 
                               's proced': 's_procedencia',
                               'ap': 'ap',
                               'otros': 'otros',
                               'diag principal': 'diagnostico',
                               'motivo ing': 'motivo_ing',
                               'agudo estable': 'agudo_estable',    # Posible otros
                               'crónico reag': 'cronico_reag',      # Posible otros
                               'paliativo onc': 'paliativo_onc_noc', 
                               'pal no onc': 'paliativo_no_onc_noc',
                               'trato antibiótico': "trato_antibiotico",
                               'dolor': 'dolor',
                               'delirium': 'delirium',
                               'disnea': 'disnea',
                               'ast-anorx': 'ast_anorx',     # Agrupan astenia y anorexia (en 17,18 y 19 la separaban)
                               'fiebre': 'fiebre',
                               'transfusion': 'transfusion',        # Posible otros
                               'paracentesis': 'paracentesis',      # Posible otros
                               'toracocentesis': 'toracocentesis',
                               'ps/ik': 'ps_ecog',
                               'barthel': 'barthel',
                               'gds-fast': 'gds_fast',
                               'otros/complicaciones': 'otros_complicaciones',
                               'agonía': 'agonia',
                               'sedación': 'sedacion',
                               'motivo alta': 'motivo_alta',
                               'n.º estancias': "n_estancias",
                               'n.º visitas': "n_visitas",
                               'ayuntamiento': 'ayuntamiento',          # Se empieza a incluir en el 2020
                               'médico': 'medico'})

data_2021 = df_21.rename(columns={'h proced': 'h_procedencia', 
                               's proced': 's_procedencia',
                               'ap': 'ap',
                               'otros': 'otros',
                               'diag principal': 'diagnostico',
                               'motivo ing': 'motivo_ing',
                               'agudo estable': 'agudo_estable',    # Posible otros
                               'crónico reag': 'cronico_reag',      # Posible otros
                               'paliativo onc': 'paliativo_onc_noc', 
                               'pal no onc': 'paliativo_no_onc_noc',
                               'trato antibiótico': "trato_antibiotico",
                               'dolor': 'dolor',
                               'delirium': 'delirium',
                               'disnea': 'disnea',
                               'ast-anorx': 'ast_anorx',     # Agrupan astenia y anorexia (en 17,18 y 19 la separaban)
                               'fiebre': 'fiebre',
                               'transfusion': 'transfusion',        # Posible otros
                               'paracentesis': 'paracentesis',      # Posible otros
                               'toracocentesis': 'toracocentesis',
                               'ps/ik': 'ps_ecog',
                               'barthel': 'barthel',
                               'gds-fast': 'gds_fast',
                               'otros/complicaciones': 'otros_complicaciones',
                               'agonia': 'agonia',
                               'sedación': 'sedacion',
                               'motivo alta': 'motivo_alta',
                               'n.º estancias': "n_estancias",
                               'n.º visitas': "n_visitas",
                               'ayuntamiento': 'ayuntamiento',          # Se empieza a incluir en el 2020
                               'médico': 'medico'})
                               
data_2022 = df_22.rename(columns={'fecha de alta': 'fecha_alta', 
                               'h.procedencia': 'h_procedencia',
                               'servicio': 's_procedencia',
                               'ap': 'ap',
                               'motivo ing': 'motivo_ing',
                               'diagnóstico principal': 'diagnostico',
                               'agudo estable': 'agudo_estable',    # Posible otros
                               'crónico agud.': 'cronico_reag',      # Posible otros
                               'paliativo onc': 'paliativo_onc_noc', 
                               'palt no onc': 'paliativo_no_onc_noc',
                               'antibiotico iv': "trato_antibiotico",
                               'dolor': 'dolor',
                               'disnea': 'disnea',
                               's febril': 'fiebre',
                               'delirium': 'delirium',
                               'astenia/anorexia': 'ast_anorx', # Agrupan astenia y anorexia (en 17,18 y 19 la separaban)
                               'fe iv': 'fe_iv',          # Se añade en 2022                                                    
                               'transf': 'transfusion',        # Posible otros
                               'paracen': 'paracentesis',      # Posible otros
                               'toracocen': 'toracocentesis',
                               'ps/ecog': 'ps_ecog',
                               'barthel': 'barthel',
                               'gds/fast': 'gds_fast',
                               'sedación': 'sedacion',
                               'motivo alta': 'motivo_alta',
                               'n.º estancias': "n_estancias",
                               'n.º visitas': "n_visitas",
                               'ayuntamiento': 'ayuntamiento',          # Se empieza a incluir en el 2020
                               'médico': 'medico'})


## 3.2. Year por dataframe

- Creamos una nueva columna year para cada dataframe y añadimos a nueva lista

In [13]:
data_2017["year"] = 2017
data_2018["year"] = 2018
data_2019["year"] = 2019
data_2020["year"] = 2020
data_2021["year"] = 2021
data_2022["year"] = 2022

all_data_rename = [data_2017, data_2018, data_2019 ,data_2020, data_2021, data_2022]

In [14]:
# Observamos la información de cada dataframe para asegurarnos que tienen todas el mismo nombre y vemos su forma (shape)
for i, data in enumerate(all_data_rename):
    i += 2017
    print("Datos del año",i)
    print(data.shape)
    print(data.info())
    print("="*80)

Datos del año 2017
(587, 30)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 587 entries, 0 to 586
Data columns (total 30 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   h_procedencia         586 non-null    object 
 1   s_procedencia         587 non-null    object 
 2   ap                    586 non-null    object 
 3   otros                 587 non-null    object 
 4   diagnostico           587 non-null    object 
 5   motivo_ing            587 non-null    object 
 6   paliativo_onc_noc     586 non-null    object 
 7   paliativo_no_onc_noc  586 non-null    object 
 8   fiebre                587 non-null    object 
 9   disnea                586 non-null    object 
 10  dolor                 587 non-null    object 
 11  delirium              587 non-null    object 
 12  astenia               587 non-null    object 
 13  anorexia              587 non-null    object 
 14  otros_1               587 non-null    object 

## 3.3. Seleccionar y eliminar columnas o valores no deseados

**Pasos:**
* Eliminamos la columna `unnamed.1` No conocemos que representan los 5 valores unnamed de los datos de 2017.
* La columna de `astenia` y `anorexia` viene a partir del 2020 agrupada.
  * Agrupar los datos de `astenia` y `anorexia` del 17 al 19 antes del `concat` y renombrar la columna por `ast_anorx` 
* Eliminamos valores atípicos de `n_estancias`

**Insights:**
* La columna de `trato_anibiotico` solo está a partir del 2020 se mantiene pero solo para esos años.

In [15]:
# Quitamos columnas innecesarias 

data_2017.drop(columns="unnamed.1", inplace=True)  
# Unnamed no tiene valores importantes sólo 5 valores numéricos que no sabemos a que pertenecen
# unnamed.1 [nan 2.840000e+02 2.121425e+06 2.078874e+06 2.130000e+02 2.790000e+02]

In [17]:
# Función para agrupar las columnas de astenia y anorexia porque se agrupan en los datos de 2020 en adelante

def col_astenia_anorexia(dataframes: list) -> pd.DataFrame:
    for df in dataframes:
        df['ast_anorx'] = np.where(df['astenia']=='si', 'si', df['anorexia'])
        df = df.drop(['astenia', 'anorexia'],axis=1, inplace=True)
        
# Agrupamos astenia y anorexia en una lista con los df que tienen astenia y anorexia separados
astenia_anorexia = [data_2017, data_2018, data_2019]

col_astenia_anorexia(astenia_anorexia)

In [30]:
# Ahora que hemos cambiado las columnas de 2017 a 2019 las almacenamos en una nueva lista

all_data = [data_2017, data_2018, data_2019 ,data_2020, data_2021, data_2022]

In [32]:
# Observamos los valores de n_estancias

for i, data in enumerate(all_data):
    try:
        # Convierte los valores a numericos
        data['n_estancias'] = pd.to_numeric(data['n_estancias'], errors='coerce')

        # Obtenemos los valores únicos y ordenados de la columna 'n_estancias' de mayor a menor, ignorando los valores NaN
        unique_sorted_values = np.sort(data['n_estancias'].dropna().unique())[::-1]

        print(f"Data_{2017+i} unique sorted 'n_estancias':\n{unique_sorted_values}\n")
    except KeyError:
        print(f"Data_{2017+i} does not have 'n_estancias' column\n")


Data_2017 unique sorted 'n_estancias':
[141. 103. 100.  98.  96.  92.  87.  74.  71.  69.  68.  67.  58.  56.
  55.  51.  50.  49.  48.  47.  46.  45.  42.  41.  40.  39.  38.  37.
  36.  35.  34.  33.  32.  31.  30.  29.  28.  27.  26.  25.  24.  23.
  22.  21.  20.  19.  18.  17.  16.  15.  14.  13.  12.  11.  10.   9.
   8.   7.   6.   5.   4.   3.   2.   1.   0.]

Data_2018 unique sorted 'n_estancias':
[304. 180. 135. 111. 106. 104.  99.  86.  84.  79.  78.  77.  76.  75.
  74.  73.  72.  70.  65.  64.  63.  61.  60.  58.  57.  56.  55.  54.
  53.  52.  51.  50.  48.  46.  45.  44.  43.  42.  39.  38.  37.  36.
  35.  34.  33.  32.  31.  30.  29.  28.  27.  26.  25.  24.  23.  22.
  21.  20.  19.  18.  17.  16.  15.  14.  13.  12.  11.  10.   9.   8.
   7.   6.   5.   4.   3.   2.   1.   0.]

Data_2019 unique sorted 'n_estancias':
[161. 140. 130. 126. 119.  90.  84.  78.  72.  71.  66.  64.  58.  57.
  56.  55.  45.  44.  43.  42.  38.  37.  36.  35.  34.  33.  32.  31.
  30.  29. 

In [41]:
# Elimino el valor atípico
data_2022 = data_2022[data_2022['n_estancias'] != 2.793914e+06]

# Convierto los valores a numericos
data_2022['n_estancias'] = pd.to_numeric(data_2022['n_estancias'], errors='coerce')

# Obtengo los valores únicos y ordenados de la columna 'n_estancias' de mayor a menor, ignorando los valores NaN
unique_sorted_values = np.sort(data_2022['n_estancias'].dropna().unique())[::-1]

print(f"Data_2022 unique sorted 'n_estancias':\n{unique_sorted_values}\n")


Data_2022 unique sorted 'n_estancias':
[188. 171. 166. 154. 133. 125. 118. 117. 107. 102. 101. 100.  97.  92.
  89.  80.  79.  78.  77.  71.  70.  66.  65.  63.  62.  61.  60.  59.
  58.  56.  54.  53.  52.  51.  50.  49.  48.  46.  45.  44.  43.  42.
  41.  40.  39.  38.  37.  36.  35.  34.  33.  32.  31.  30.  29.  28.
  27.  26.  25.  24.  23.  22.  21.  20.  19.  18.  17.  16.  15.  14.
  13.  12.  11.  10.   9.   8.   7.   6.   5.   4.   3.   2.   1.]



In [42]:
# Realizamos otro check para ver los datos de n_visitas
for i, data in enumerate(all_data):
    try:
        # Convierte los valores a numericos
        data['n_visitas'] = pd.to_numeric(data['n_visitas'], errors='coerce')

        # Obtén los valores únicos y ordenados de la columna 'n_estancias' de mayor a menor, ignorando los valores NaN
        unique_sorted_values = np.sort(data['n_visitas'].dropna().unique())[::-1]

        print(f"Data_{2017+i} unique sorted 'n_visitas':\n{unique_sorted_values}\n")
    except KeyError:
        print(f"Data_{2017+i} does not have 'n_visitas' column\n")


Data_2017 unique sorted 'n_visitas':
[48. 45. 40. 37. 35. 34. 33. 31. 28. 24. 23. 22. 21. 20. 18. 17. 16. 15.
 14. 13. 12. 11. 10.  9.  8.  7.  6.  5.  4.  3.  2.  1.  0.]

Data_2018 unique sorted 'n_visitas':
[60. 40. 35. 34. 33. 31. 30. 27. 26. 25. 22. 21. 20. 19. 18. 17. 16. 15.
 14. 13. 12. 11. 10.  9.  8.  7.  6.  5.  4.  3.  2.  1.  0.]

Data_2019 unique sorted 'n_visitas':
[50. 43. 40. 36. 30. 25. 24. 23. 22. 20. 19. 18. 17. 16. 15. 14. 13. 12.
 11. 10.  9.  8.  7.  6.  5.  4.  3.  2.  1.  0.]

Data_2020 unique sorted 'n_visitas':
[56. 51. 42. 41. 40. 36. 33. 31. 30. 29. 28. 27. 26. 25. 23. 22. 21. 20.
 19. 18. 17. 16. 15. 14. 13. 12. 11. 10.  9.  8.  7.  6.  5.  4.  3.  2.
  1.  0.]

Data_2021 unique sorted 'n_visitas':
[71. 54. 42. 41. 40. 34. 32. 31. 30. 27. 26. 25. 24. 23. 22. 21. 20. 19.
 18. 17. 16. 15. 14. 13. 12. 11. 10.  9.  8.  7.  6.  5.  4.  3.  2.  1.
  0.]

Data_2022 unique sorted 'n_visitas':
[99. 80. 76. 68. 50. 49. 44. 43. 42. 40. 39. 38. 37. 36. 35. 31. 30. 28.

In [43]:
# Como hemos modificado los datos de un daframe los guardamos de nuevo en la lista

all_data = [data_2017, data_2018, data_2019 ,data_2020, data_2021, data_2022]

In [45]:
# Check para ver los valores de n_estancias

for i, data in enumerate(all_data):
    try:
        data['n_estancias'] = pd.to_numeric(data['n_estancias'], errors='coerce')

        unique_sorted_values = np.sort(data['n_estancias'].dropna().unique())[::-1]

        print(f"Data_{2017+i} unique sorted 'n_estancias':\n{unique_sorted_values}\n")
    except KeyError:
        print(f"Data_{2017+i} does not have 'n_estancias' column\n")

Data_2017 unique sorted 'n_estancias':
[141. 103. 100.  98.  96.  92.  87.  74.  71.  69.  68.  67.  58.  56.
  55.  51.  50.  49.  48.  47.  46.  45.  42.  41.  40.  39.  38.  37.
  36.  35.  34.  33.  32.  31.  30.  29.  28.  27.  26.  25.  24.  23.
  22.  21.  20.  19.  18.  17.  16.  15.  14.  13.  12.  11.  10.   9.
   8.   7.   6.   5.   4.   3.   2.   1.   0.]

Data_2018 unique sorted 'n_estancias':
[304. 180. 135. 111. 106. 104.  99.  86.  84.  79.  78.  77.  76.  75.
  74.  73.  72.  70.  65.  64.  63.  61.  60.  58.  57.  56.  55.  54.
  53.  52.  51.  50.  48.  46.  45.  44.  43.  42.  39.  38.  37.  36.
  35.  34.  33.  32.  31.  30.  29.  28.  27.  26.  25.  24.  23.  22.
  21.  20.  19.  18.  17.  16.  15.  14.  13.  12.  11.  10.   9.   8.
   7.   6.   5.   4.   3.   2.   1.   0.]

Data_2019 unique sorted 'n_estancias':
[161. 140. 130. 126. 119.  90.  84.  78.  72.  71.  66.  64.  58.  57.
  56.  55.  45.  44.  43.  42.  38.  37.  36.  35.  34.  33.  32.  31.
  30.  29. 

In [47]:
# Observo el número total de datos y voy acumulandolo por datframe
total = 0
for i, df in enumerate(all_data):
    i += 2017
    total += len(df)
    print("df", i)
    print(len(df.columns), df.columns)
    print(total, " Datos acumulados")
    print("="*80)

df 2017
28 Index(['h_procedencia', 's_procedencia', 'ap', 'otros', 'diagnostico',
       'motivo_ing', 'paliativo_onc_noc', 'paliativo_no_onc_noc', 'fiebre',
       'disnea', 'dolor', 'delirium', 'otros_1', 'p_terminal', 'agonia',
       'ps_ecog', 'barthel', 'gds_fast', 'eva_ing', 'otros_2',
       'otros_complicaciones', 'n_estancias', 'n_visitas', 'sedacion',
       'motivo_alta', 'medico', 'year', 'ast_anorx'],
      dtype='object')
587  Datos acumulados
df 2018
28 Index(['h_procedencia', 's_procedencia', 'ap', 'otros', 'diagnostico',
       'motivo_ing', 'paliativo_onc_noc', 'paliativo_no_onc_noc', 'fiebre',
       'disnea', 'dolor', 'delirium', 'otros_1', 'p_terminal', 'agonia',
       'ps_ecog', 'barthel', 'gds_fast', 'eva_ing', 'otros_2',
       'otros_complicaciones', 'n_estancias', 'n_visitas', 'sedacion',
       'motivo_alta', 'medico', 'year', 'ast_anorx'],
      dtype='object')
1123  Datos acumulados
df 2019
28 Index(['h_procedencia', 's_procedencia', 'ap', 'otros', 'diagn

# 4. Concat de los dataframes

Ahora que tenemos todas las columnas con el mismo nombre podemos realizar un `concat` y trabajar sobre un único dataframe

In [48]:
df_concat = pd.concat(all_data, ignore_index=True, axis=0)

In [49]:
# Vemos la forma del dataframe
df_concat.shape

(4013, 37)

In [29]:
# Guardo una copia en csv de los datos concatenados en data

df_concat.to_csv(path_or_buf= "../data/02_intermediate/HADO_concat.csv", sep="^", index=False)

In [50]:
# Podemos cargar los datos desde Kedro

df = catalog.load('hado_concat')

[09/06/23 16:49:50] INFO     Loading data from 'hado_concat' (CSVDataSet)...                    data_catalog.py:345

In [51]:
df.head()

h_procedencia s_procedencia  ap otros                  diagnostico  \
0   gil casares          upal  no    no                       ca orl   
1       clinico           ONC  no    no              Melanoma vulvar   
2       clinico           MIR  no    no              ca broncogenico   
3       clinico           DIG  no    no            cirrosis hepatica   
4       clinico           URG  no    no  neplasia de mama estadio IV   

                   motivo_ing paliativo_onc_noc paliativo_no_onc_noc fiebre  \
0           contro d sintomas                si                   si     no   
1           mal control dolor                si                   no     no   
2           control evolutivo                si                   si     no   
3  admininistacion octreotido                no                   no     no   
4         control de sintomas                si                   no     no   

  disnea dolor delirium otros_1 p_terminal agonia ps_ecog barthel gds_fast  \
0     no    si       no      no         si     no     4.0    30.0       no   
1     no    si       no      no         si     no     3-4      no       no   
2     si    no       no      no         no     no     3-4    40.0       no   
3     no    no       no      no         no     no     1.0    90.0       no   
4     si    si       no      no         si     no     4.0    30.0       no   

  eva_ing otros_2      otros_complicaciones  n_estancias  n_visitas sedacion  \
0      no      no    reingreso en urgencias           21         10       no   
1      no      no  met. pulmonares y digest           24          8       no   
2      no      no                        no           14          6       no   
3      no      no                        no            1          1       no   
4     7.0      no                        no            2          1       no   

       motivo_alta         medico  year ast_anorx agudo_estable cronico_reag  \
0       reingreso          valdes  2017        si           NaN          NaN   
1           exitus    galego feal  2017        si           NaN          NaN   
2  fin de cuidados  lopez renedo.  2017        no           NaN          NaN   
3  fin de cuidados  lopez renedo.  2017        no           NaN          NaN   
4           exitus  lopez renedo.  2017        no           NaN          NaN   

  trato_antibiotico transfusion paracentesis toracocentesis ayuntamiento  \
0               NaN         NaN          NaN            NaN          NaN   
1               NaN         NaN          NaN            NaN          NaN   
2               NaN         NaN          NaN            NaN          NaN   
3               NaN         NaN          NaN            NaN          NaN   
4               NaN         NaN          NaN            NaN          NaN   

  fecha_alta fe_iv  
0        NaN   NaN  
1        NaN   NaN  
2        NaN   NaN  
3        NaN   NaN  
4        NaN   NaN

In [52]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4013 entries, 0 to 4012
Data columns (total 37 columns):
 #   Column                Non-Null Count  Dtype 
---  ------                --------------  ----- 
 0   h_procedencia         4012 non-null   object
 1   s_procedencia         4013 non-null   object
 2   ap                    4012 non-null   object
 3   otros                 2958 non-null   object
 4   diagnostico           4010 non-null   object
 5   motivo_ing            4002 non-null   object
 6   paliativo_onc_noc     4012 non-null   object
 7   paliativo_no_onc_noc  4011 non-null   object
 8   fiebre                4011 non-null   object
 9   disnea                4012 non-null   object
 10  dolor                 4013 non-null   object
 11  delirium              4012 non-null   object
 12  otros_1               1549 non-null   object
 13  p_terminal            1547 non-null   object
 14  agonia                2955 non-null   object
 15  ps_ecog               4012 non-null   

# 5. Limpieza de datos

La limpieza de datos es un paso crucial en el proceso de análisis de datos y aprendizaje automático. A menudo, los datos recopilados desde diferentes fuentes pueden contener errores, inconsistencias, valores faltantes y datos redundantes que pueden afectar negativamente el resultado del análisis o del modelo de aprendizaje automático. Aquí hay algunas razones para realizar la limpieza de datos:

### Mejorar la calidad de los datos
Los datos sucios o inexactos pueden llevar a conclusiones erróneas. La limpieza mejora la calidad de los datos al eliminar o corregir registros erróneos.

### Manejar valores faltantes
Los valores faltantes pueden distorsionar la interpretación y el resultado del análisis. Se pueden utilizar diversas técnicas para manejarlos, como la imputación de datos.

### Consistencia y formato estándar
Asegurarte de que los datos estén en un formato estándar es crucial para realizar análisis o aplicar algoritmos de aprendizaje automático. Por ejemplo, las fechas deberían estar en un formato uniforme, y las categorías similares deberían ser coherentes en la terminología.

### Eliminar duplicados
Los registros duplicados pueden sesgar los resultados del análisis. Es esencial eliminar o corregir estos registros para obtener una vista más precisa de los datos.

### Preparación para el análisis o modelado
Muchos algoritmos de aprendizaje automático requieren que los datos estén en un formato específico y que ciertas suposiciones se cumplan. La limpieza de datos te ayuda a preparar tus datos para estos algoritmos.

### Reducción del tamaño de los datos
Al eliminar registros redundantes o irrelevantes, también puedes hacer que el conjunto de datos sea más pequeño y más fácil de manejar, lo que a su vez puede acelerar el análisis.

### Identificación de errores o anomalías
El proceso de limpieza a menudo ayuda a identificar errores en la recopilación de datos o en los procesos de negocio que pueden necesitar ser corregidos.

>En resumen, la limpieza de datos es una etapa esencial para asegurarte de que tu análisis sea preciso, tus modelos sean robustos y tus decisiones basadas en datos sean sólidas.

## 5.1.Strip, Lower, remove punctuation marks and accents
 
* Quitar espacios
* Todo a minúsculas
* Quitar signos de puntuación y tildes

In [56]:
# Funcion para limpiar los datos del dataframe

def clean_text(df):
    
    def data_strip(df):
        '''Quitamos los espacios del principio y final de los datos, y los espacios extra entre palabras'''
        for column in df:
            if df[column].dtype == 'object':  # Solo se aplica a columnas de tipo 'object' (string)
                df[column] = df[column].replace('\\s+', ' ', regex=True).str.strip()


    def to_lowercase(df):
        '''Pasamos todo a minúsculas'''
        for column in df:
            if df[column].dtype == 'object':  # comprueba si la columna es de tipo 'object'
                df[column] = df[column].str.lower()

    def remove_punctuation_and_accents(df):
        '''Quitamos tildes y signos de puntuación'''
        for column in df:
            if df[column].dtype == 'object':  # comprueba si la columna es de tipo 'object'
                df[column] = df[column].apply(lambda x: unidecode.unidecode(x) if isinstance(x, str) else x)  # quita las tildes
                df[column] = df[column].str.translate(str.maketrans("", "", string.punctuation))  # quita los signos de puntuación

    data_strip(df)
    to_lowercase(df)
    remove_punctuation_and_accents(df)

# Aplicamos la función al dataframe  
clean_text(df)

In [57]:
# Función "check" para ver los valores únicos de cada columna
def unicos(df):
    columns = df.columns.tolist()
    for i, column in enumerate(columns):
        v_column = df[column].unique()
        print(df.columns.values[i])
        print(len(v_column), v_column)
        print("="*66)
        
unicos(df)

h_procedencia
27 ['gil casares' 'clinico' 'no' 'provincial' 'hula' 'conxo' 'chuac'
 'clincio' 'clnico' 'si' 'cliinico' nan 'salnes' 'rosaleda' 'clincico'
 'hgc' 'hcg' 'ap' 'san rafael la coruna' 'quiron la coruna' 'clinicoap'
 'clinoco' 'lucus augusti' 'hm' 'residencia' 'pontevedra' 'hm rosaleda']
s_procedencia
169 ['upal' 'onc' 'mir' 'dig' 'urg' 'no' 'hem' 'tra' 'rdt' 'nml' 'mirp' 'cgd'
 'ume' 'cot' 'nmlp' 'acv' 'umap' 'nef' 'nof' 'cardiologia' 'car' 'nrl'
 'mirg' 'ncr' 'neumo' 'card' 'uro' 'gine' 'psqg' 'hematol' 'mir conxo'
 'oncologia' 'nefrologia' 'digestivo' 'hematologia' 'urgencias'
 'cirugia vascular' 'orl' 'neumologia' 'neuro' 'urologia' 'neurc'
 'eif mir' 'cgdurg' 'mirpro' 'cirugia general' 'hospital de dia'
 'consulta ela multidisciplinar' 'urgrn' 'mir gil casares no'
 'mirap protocolo hierro en domicilio' 'reumatologia'
 'nmlconsultas esterna' 'nmlurg' 'nmlcosultas externas' 'hado' 'oncurg'
 'oncconsultas' 'nmlconsutas externas' 'urgonc' 'hdd nml' 'end' 'rtp'
 'urgurg' 'inf

## 5.2. Valores NA

Observaré si existen valores nulos o faltantes en el dataframe

Puede verse sumando los valores o en porcentajes

In [67]:
print(f"Total de valores faltantes por columna:\n{df.isna().sum().sort_values(ascending=False)}")

Total de valores faltantes por columna:
fecha_alta              3247
fe_iv                   2959
p_terminal              2466
otros_2                 2465
eva_ing                 2465
otros_1                 2464
agudo_estable           1551
ayuntamiento            1551
toracocentesis          1551
transfusion             1550
cronico_reag            1550
trato_antibiotico       1550
paracentesis            1550
agonia                  1058
otros_complicaciones    1057
otros                   1055
motivo_ing                11
sedacion                   5
diagnostico                3
fiebre                     2
paliativo_no_onc_noc       2
motivo_alta                1
ap                         1
medico                     1
h_procedencia              1
paliativo_onc_noc          1
barthel                    1
ps_ecog                    1
delirium                   1
disnea                     1
n_visitas                  0
year                       0
ast_anorx                  0
s_p

In [37]:
# Encuentra las columnas con valores faltantes y su porcentaje de valores faltantes
missing_values = df.isnull().sum()
missing_percentage = missing_values / len(df) * 100

print("Porcentaje de valores faltantes por columna:")
print(round(missing_percentage.sort_values(ascending=False),2))

Porcentaje de valores faltantes por columna:
fecha_alta              80.91
fe_iv                   73.74
p_terminal              61.45
otros_2                 61.43
eva_ing                 61.43
otros_1                 61.40
ayuntamiento            38.65
toracocentesis          38.65
agudo_estable           38.65
paracentesis            38.62
transfusion             38.62
trato_antibiotico       38.62
cronico_reag            38.62
agonia                  26.36
otros_complicaciones    26.34
otros                   26.29
n_visitas                0.65
motivo_ing               0.27
n_estancias              0.17
sedacion                 0.12
diagnostico              0.07
paliativo_no_onc_noc     0.05
fiebre                   0.05
ps_ecog                  0.02
ap                       0.02
disnea                   0.02
delirium                 0.02
h_procedencia            0.02
medico                   0.02
motivo_alta              0.02
barthel                  0.02
paliativo_onc_noc        

## 5.3. Como tratar los valores faltantes (NaN)

Dependiendo del porcentaje de valores faltantes, se puede optar por:
- **Eliminar las columnas con un alto porcentaje de valores faltantes**
- **Eliminar los registros con valores faltantes** 
- **Imputarlos** utilizando la **media**, **mediana**, **moda** o algún otro método de imputación como algún `valor` o `string`.

### 5.3.1. Imputar valores
Para diagnóstico y otras columnas rellenamos con string `desconocido` para luego hacer los **replaces**
Aplicaremos con string `no` y `vacio` y 0 para otras columnas con el mismo método de `fillna`

In [70]:
# Version resumida
replacement_dict = {
    'desconocido': ['diagnostico', 'motivo_ing', 'motivo_alta', 'medico', 'sedacion', 'ayuntamiento', 'otros_2'],
    'no': ['h_procedencia', 'otros', 'otros_1', 'otros_complicaciones'],
    'vacio': ['fe_iv', 'toracocentesis', 'paracentesis', 'transfusion', 'trato_antibiotico', 'cronico_reag', 'agudo_estable', 'ast_anorx', 'agonia', 'p_terminal', 'delirium', 'dolor', 'disnea', 'fiebre', 'paliativo_no_onc_noc', 'paliativo_onc_noc', 'ap', 'fecha_alta'],
    0: ['gds_fast', 'eva_ing', 'barthel', 'ps_ecog']
}

for value, columns in replacement_dict.items():
    df[columns] = df[columns].fillna(value)

In [71]:
df.isna().sum().sort_values(ascending=False)

h_procedencia           0
otros_2                 0
n_estancias             0
n_visitas               0
sedacion                0
motivo_alta             0
medico                  0
year                    0
ast_anorx               0
agudo_estable           0
cronico_reag            0
trato_antibiotico       0
transfusion             0
paracentesis            0
toracocentesis          0
ayuntamiento            0
fecha_alta              0
otros_complicaciones    0
eva_ing                 0
s_procedencia           0
gds_fast                0
ap                      0
otros                   0
diagnostico             0
motivo_ing              0
paliativo_onc_noc       0
paliativo_no_onc_noc    0
fiebre                  0
disnea                  0
dolor                   0
delirium                0
otros_1                 0
p_terminal              0
agonia                  0
ps_ecog                 0
barthel                 0
fe_iv                   0
dtype: int64

Aquí otro método de rellenar los valores NAN reemplazando por columnas

```python
# Rellenamos para los NAs con el valor 'no
df[
    ['h_procedencia',
     'otros',
     'otros_1',
     'otros_complicaciones'
    ]
]= df[
    ['h_procedencia',
     'otros',
     'otros_1',
     'otros_complicaciones'
    ]
].fillna('no')

# Rellenamos para los NAs en blanco
df[
    ['fe_iv', 
    'toracocentesis', 
    'paracentesis', 
    'transfusion',
    'trato_antibiotico',
    'cronico_reag',
    'agudo_estable',
    'ast_anorx',
    'agonia',
    'p_terminal',
    'delirium',
    'dolor',
    'disnea',
    'fiebre',
    'paliativo_no_onc_noc',
    'paliativo_onc_noc',
    'ap',
    'fecha_alta'
   ]
  ] = df[
    ['fe_iv', 
    'toracocentesis', 
    'paracentesis', 
    'transfusion',
    'trato_antibiotico',
    'cronico_reag',
    'agudo_estable',
    'ast_anorx',
    'agonia',
    'p_terminal',
    'delirium',
    'dolor',
    'disnea',
    'fiebre',
    'paliativo_no_onc_noc',
    'paliativo_onc_noc',
    'ap',
    'fecha_alta'
   ]
  ].fillna('')
```

### 5.3.2. Visitas y estancias

* Para pasar las visitas y estancias a números tenemos que rellenar los NA. **Seleccionar un método**: **media, moda o mediana**
* Este paso lo hemos realizado en el paso [3.3. Seleccionar y eliminar columnas o valores no deseados](#3.3.-Seleccionar-y-elimianr-columnas-o-valores-no-deseados) pero plantearemos todos los escenarios en este apartado.

In [44]:
# Pasar n_estancias y n_visitas a número
df["n_estancias"] = pd.to_numeric(df["n_estancias"], errors='coerce')
df["n_visitas"] = pd.to_numeric(df["n_visitas"], errors='coerce')

# Rellenamos con la media para los NAs
df['n_estancias'] = df['n_estancias'].fillna(df['n_estancias']\
                                     .mean())
df['n_visitas'] = df['n_visitas'].fillna(df['n_visitas']\
                                 .mean())

# Rellenamos con la moda para los NAs
# df['n_estancias'] = df['n_estancias'].fillna(df['n_estancias'].mode()[0])
# df['n_visitas'] = df['n_visitas'].fillna(df['n_visitas'].mode()[0])

# Rellenamos con la mediana para los NAs
# df['n_estancias'] = df['n_estancias'].fillna(df['n_estancias'].median())
# df['n_visitas'] = df['n_visitas'].fillna(df['n_visitas'].median())

In [74]:
# Seleccionado el método entre media, mediana o moda los pasamos a tipo de datos enteros

df = df.astype({'n_estancias': 'int64', 'n_visitas': 'int64'})

>Ahora que hemos reemplazado todos los NA podemos ver la proporción de valores que hay en cada columna del dataframe

In [75]:
# Función para ver la proporción de valores por columna en el dataframe
def value_counts_normalized(df):
    for column in df.columns:
        print(round(df[column].value_counts(normalize=True)\
                              .sort_values(ascending=False), ndigits=3))
        
value_counts_normalized(df)

clinico                 0.544
no                      0.312
conxo                   0.082
gil casares             0.036
clincio                 0.011
provincial              0.003
hgc                     0.002
cliinico                0.002
chuac                   0.001
residencia              0.001
si                      0.001
clnico                  0.000
hula                    0.000
san rafael la coruna    0.000
salnes                  0.000
rosaleda                0.000
hcg                     0.000
ap                      0.000
hm                      0.000
clincico                0.000
clinicoap               0.000
clinoco                 0.000
lucus augusti           0.000
pontevedra              0.000
quiron la coruna        0.000
hm rosaleda             0.000
Name: h_procedencia, dtype: float64
no                                     0.305
mir                                    0.120
onc                                    0.118
urg                                    0.096
upal

# 6. Replaces:

1. **Regex**: Busco utilizando expresiones regulares (regex) palabras para agrupar diagnósticos
Por ejemplo: Cancer
2. **Replace**: A través del uso de diccionarios modifico los valores para corregirlos

## 6.1. Búsqueda de palabras

Busco y cuento los valores que coincidan 
Esto es uno de los pasos que se realizan en el EDA

In [76]:
words = ['cancer']

# Convierte la lista de palabras en una expresión regular
regex = r'\b(?:{})\b'.format('|'.join(words))
df['diagnostico'].str.contains(regex, case=False, regex=True)\
                 .value_counts()

False    3662
True      351
Name: diagnostico, dtype: int64

In [51]:
words = ['itu']

# Convierte la lista de palabras en una expresión regular
regex = r'\b(?:{})\b'.format('|'.join(words))
df['diagnostico'].str.contains(regex, case=False, regex=True)\
                 .value_counts()

False    3795
True      218
Name: diagnostico, dtype: int64

In [52]:
words = ['icc']

# Convierte la lista de palabras en una expresión regular
regex = r'\b(?:{})\b'.format('|'.join(words))
df['diagnostico'].str.contains(regex, case=False, regex=True)\
                 .value_counts()

False    3916
True       97
Name: diagnostico, dtype: int64

## 6.2. Replace `diagnostico`

Diccionario de valores de la columna `diagnostico` y replace a través de **regex**

In [77]:
# Crear un diccionario de palabras a buscar y reemplazar
replacement_dict = {
    'iccbacteriemia': 'insuficiencia cardiaca cronica bacteriemia',
    'icc': 'insuficiencia cardiaca cronica',
    'ic': 'insuficiencia cardiaca',
    'insf ': 'insuficiencia',
    'i cardiaca': 'insuficiencia cardiaca',
    'icardiaca': 'insuficiencia cardiaca',
    'insufcardiaca': 'insuficiencia cardiaca',
    'insuficienciacardiaca': 'insuficiencia cardiaca',
    '1tu': 'ITU (infeccion del tracto urinario)',
    'itu': 'ITU (infeccion del tracto urinario)',
    'ituinfeccion': 'infeccion',
    'inf': 'infeccion',
    'infecc': 'infeccion',
    'infecion': 'infeccion',
    'infec': 'infeccion',
    'capulmon': 'cancer pulmon',
    'canc': 'cancer',
    'ca': 'cancer',
    'insuf': 'insuficiencia',
    'est': 'estadio',
    'e': 'estadio',
    'fr': 'fractura',
    'deteriorocognitivo': 'deterioro cognitivo',
    'iv': 'IV',
    'resp': 'respiratoria',
    '0steomielitis': 'osteomielitis',
}

# Buscar y reemplazar cada palabra en el DataFrame utilizando el diccionario
for word, replacement in replacement_dict.items():
    df['diagnostico'] = df['diagnostico'].str.replace(r'\b{}\b'.format(word), replacement, case=False, regex=True)

In [59]:
words = ['pulmon']

# Convierte la lista de palabras en una expresión regular
regex = r'\b(?:{})\b'.format('|'.join(words))
df['diagnostico'].str.contains(regex, case=False, regex=True)\
                 .value_counts()

False    3792
True      221
Name: diagnostico, dtype: int64

In [60]:
df['diagnostico'].value_counts()

ITU (infeccion del tracto urinario)                                                                                                                                                                                             172
infeccion respiratoria                                                                                                                                                                                                          145
infeccion urinaria                                                                                                                                                                                                              112
insuficiencia cardiaca                                                                                                                                                                                                           73
cancer de colon                                                                         

## 6.3. Replace general y h_procedencia

* Hospital procedencia
* Genéricos [si, no, clinico]

In [81]:
# Observo los valores unicos para la columna h_procedencia

df['h_procedencia'].unique()

array(['gil casares', 'clinico', 'no', 'provincial', 'hula', 'conxo',
       'chuac', 'clincio', 'clnico', 'si', 'cliinico', 'salnes',
       'rosaleda', 'clincico', 'hgc', 'hcg', 'ap', 'san rafael la coruna',
       'quiron la coruna', 'clinicoap', 'clinoco', 'lucus augusti', 'hm',
       'residencia', 'pontevedra', 'hm rosaleda'], dtype=object)

In [82]:
# Crear un diccionario de palabras a buscar y reemplazar
replacement_dict_general = {
    'n0': 'no',
    'np': 'no',
    'nn': 'no',
    'ono': 'no',
    'son': 'no',
    'ns': 'no',
    'o': 'no',
    'mo': 'no',
    'nop': 'no',
    'on': 'no',
    'nsi': 'si',
    'ni': 'no',
    'ssi': 'si',
    'is': 'si',
    's': 'si',
    'clincio': 'clinico',
    'clnico': 'clinico',
    'clínico': 'clinico',
    'cliinico': 'clinico',
    'clincico': 'clinico',
    'clinoco': 'clinico',
    'clinicoap': 'clinico',
}


replacement_dict_procedencia = {
    'hgc': 'gil casares',
    'hcg': 'gil casares',
    'hm rosaleda': 'rosaleda',
    'hm': 'rosaleda'
}

# Reemplazar 'si' seguido por un número con sólo el número
df.replace(r'si\s*(\d+)', r'\1' ,regex=True, inplace=True)

# Buscar y reemplazar cada palabra en el DataFrame utilizando el diccionario general
for word, replacement in replacement_dict_general.items():
    df.replace(r'\b{}\b'.format(word), replacement, regex=True, inplace=True)

In [84]:
h_procedencia_list = df['h_procedencia'].unique()
sorted(h_procedencia_list, reverse=False)

['ap',
 'chuac',
 'clinico',
 'conxo',
 'gil casares',
 'hcg',
 'hgc',
 'hm',
 'hm rosaleda',
 'hula',
 'lucus augusti',
 'no',
 'pontevedra',
 'provincial',
 'quiron la coruna',
 'residencia',
 'rosaleda',
 'salnes',
 'san rafael la coruna',
 'si']

## 6.4. Replace s_procedencia

In [89]:
s_procedencia_lista = df['s_procedencia'].unique()
print(len(s_procedencia_lista),\
      sorted(s_procedencia_lista, reverse=False))

100 ['acv', 'angiologia', 'anr', 'ap', 'cardiologia', 'cgd', 'cgdurg', 'cirugia cardiaca', 'cirugia cardiologia', 'cirugia general', 'cirugia maxilofacial', 'cirugia plastica', 'cirugia toracica', 'cirugia vascular', 'clp', 'consulta ela multidisciplinar', 'consulta hipertension', 'consulta mir', 'consultas externas cirugia plastica', 'consultas externas digestivo', 'consultas externas mir', 'consultas externas neumologia', 'consultas externas oncologia', 'consultas oncologia', 'cot', 'cpr', 'crg', 'der', 'diagestivo', 'digestivo', 'eif', 'eif  mir', 'eif mir', 'endocrinologia', 'enfermedad infecciosas', 'ginecologia', 'hado', 'hdd neumologia', 'hematologia', 'hematologia urgencias', 'hepatologia', 'hospital de dia', 'infecciosas', 'maxilofacial', 'medicina interna', 'mir', 'mir conxo', 'mir gil', 'mir gil casares no', 'mir infecciosas', 'mir p', 'mir p consultas externas', 'mir provincial', 'mirap protocolo hierro en domicilio', 'mirc', 'mireif', 'mirg', 'mirhp', 'mirlugo', 'ncr', 'ne

In [88]:
# Crear un diccionario de palabras a buscar y reemplazar
replacement_dict = {
    'con ext oncologia': 'oncologia consultas externas',
    'con ext onco': 'oncologia consultas externas',
    'oncconsultas externa': 'oncologia consultas externas',
    'oncconsultas': 'oncologia consultas externas',
    'oncol consulta externa': 'oncologia consultas externas',
    'oncourg': 'oncologia urgencias',
    'oncurg': 'oncologia urgencias',
    'urgonc': 'oncologia urgencias',
    'oncolo': 'oncologia',
    'onco': 'oncologia',
    '0nc': 'oncologia',
    'onc': 'oncologia',
    'consultas externas cplastica': 'consultas externas cirugia plastica',
    'cplastica': 'cirugia plastica',
    'cpl': 'cirugia plastica',
    'endocrino': 'endocrinologia',
    'end': 'endocrinologia',
    'urgurg':  'urgencias',
    'urgrn': 'urgencias',
    'urgcirugia': 'urgencias cirugia',
    'urg': 'urgencias',
    'ccee': 'consultas externas',
    'uro': 'urologia',
    'tramatologia': 'traumatologia',
    'trauma': 'traumatologia',
    'tra': 'traumatologia',
    'nmlconsultas esterna': 'neumologia consultas externas',
    'nmlconsutas externas': 'neumologia consultas externas',
    'nmlcosultas externas': 'neumologia consultas externas',
    'cexternas neumologia': 'neumologia consultas externas',
    'nmlurg' : 'neumologia urgencias',
    'hdd neumologia': 'hado neumologia',
    'neeumologia': 'neumologia',
    'neomologia': 'neumologia',
    'nemologia': 'neumologia',
    'neumo': 'neumologia',
    'neum': 'neumologia',
    'nmlp': 'neumologia',
    'neu': 'neumologia',
    'mnl': 'neumologia',
    'nml': 'neumologia',
    'maxilofac': 'maxilofacial',
    'cmx': 'cirugia maxilofacial',
    'cmf': 'cirugia maxilofacial',
    'urgencias nrl': 'urgencias neurología',
    'neurc': 'neurologia',
    'neuro': 'neurologia',
    'nrl': 'neurologia',
    'nof': 'nefrologia',
    'nfr': 'nefrologia',
    'reu': 'reumatologia',
    'cexternas mir': 'consultas externas mir',
    'rehab': 'rehabilitacion',
    'ccardiaca': 'cirugia cardiaca',
    'ccar': 'cirugia cardiologia',
    'cadiologia': 'cardiologia',
    'card': 'cardiologia',
    'car': 'cardiologia',
    'digstivo': 'digestivo',
    'dig': 'digestivo',
    'gine':'ginecologia',
    'gin': 'ginecologia',
    'hematoloxia': 'hematologia',
    'hematolog': 'hematologia',
    'hematol': 'hematologia',
    'hemato': 'hematologia',
    'hem': 'hematologia',
    'hemurg': 'hematologia urgencias',
    'c externas': 'consultas externas',
    'cee nefrologia':'nefrologia',
    'nef': 'nefrologia',
    'cee': 'consultas externas',
    'c': 'cirugia',
    'cvascular': 'cirugia vascular',
    'cirugia vasc': 'cirugia vascular',
    'radtp': 'radioterapia',
    'rdp': 'radioterapia',
    'rdt': 'radioterapia',
    'rtp': 'radioterapia',
    'mirpro': 'mir provincial',
    'mirp': 'mir provincial'
}

# Buscar y reemplazar cada palabra en el DataFrame utilizando el diccionario
for word, replacement in replacement_dict.items():
    df['s_procedencia'] = df['s_procedencia'].str.replace(r'\b{}\b'.format(word), replacement, case=False, regex=True)

In [90]:
# Quito espacios entre las palabras
for x in df['s_procedencia']:
    df['s_procedencia'] = df['s_procedencia'].replace('\\s+', ' ', regex=True).str.strip()

In [91]:
s_procedencia_lista = df['s_procedencia'].unique()
print(len(s_procedencia_lista),sorted(s_procedencia_lista, reverse=False))

99 ['acv', 'angiologia', 'anr', 'ap', 'cardiologia', 'cgd', 'cgdurg', 'cirugia cardiaca', 'cirugia cardiologia', 'cirugia general', 'cirugia maxilofacial', 'cirugia plastica', 'cirugia toracica', 'cirugia vascular', 'clp', 'consulta ela multidisciplinar', 'consulta hipertension', 'consulta mir', 'consultas externas cirugia plastica', 'consultas externas digestivo', 'consultas externas mir', 'consultas externas neumologia', 'consultas externas oncologia', 'consultas oncologia', 'cot', 'cpr', 'crg', 'der', 'diagestivo', 'digestivo', 'eif', 'eif mir', 'endocrinologia', 'enfermedad infecciosas', 'ginecologia', 'hado', 'hdd neumologia', 'hematologia', 'hematologia urgencias', 'hepatologia', 'hospital de dia', 'infecciosas', 'maxilofacial', 'medicina interna', 'mir', 'mir conxo', 'mir gil', 'mir gil casares no', 'mir infecciosas', 'mir p', 'mir p consultas externas', 'mir provincial', 'mirap protocolo hierro en domicilio', 'mirc', 'mireif', 'mirg', 'mirhp', 'mirlugo', 'ncr', 'nefrologia', 'n

## 6.5. Replace motivo_ing

In [92]:
motivo_ing_lista = df['motivo_ing'].unique()
print(len(motivo_ing_lista),sorted(motivo_ing_lista, reverse=False))

604 ['adiestramiento nutricion y control sintomas', 'admininistacion octreotido', 'admininistracio de antibiotico iv', 'adminiostracion duodopa', 'administacion myozime', 'administracion 5 azatadina', 'administracion aciclovir iv', 'administracion alprostadil iv', 'administracion antibiotico iv', 'administracion calcio iv', 'administracion de azacitidina', 'administracion de hierro', 'administracion de inmunoglobulinas', 'administracion de myozime', 'administracion de seguril sc', 'administracion de tratamiento antibiotico iv', 'administracion de vidaza', 'administracion furosemida iv', 'administracion ganmaglobulinas', 'administracion hierro i v', 'administracion hierro iv', 'administracion inmunoglobulinas', 'administracion sandostatin', 'administracion sandostatin lar', 'administracion seguril iv', 'administracion tratamiento antibiotico', 'administracion tratamiento antibiotico iv', 'administracion tratamiento iv', 'administracion tratamioento', 'administracion zoladex', 'agitacion

In [93]:
# Crear un diccionario de palabras a buscar y reemplazar
replacement_dict_ing = {
    'admininistracio': 'admininistracion',
    'tratamientoantibiotico': 'tratamiento antibiotico',
    'tratamientoiv': 'tratamiento IV',
    'trtatamiento': 'tratamiento',
    'trratamiento': 'tratamiento',
    'trato ': 'tratamiento',
    'trto': 'tratamiento',
    'trtamiento': 'tratamiento',
    'tratmiento': 'tratamiento',
    'tratatmiento': 'tratamiento',
    'tratamioento': 'tratamiento',
    'tratamientyo': 'tratamiento',
    'antiibiotico': 'antibiotico',
    'tsindrome': 'tratamiento sindrome',
    'tto ': 'tratamiento',
    'anemiatransfusion': 'anemia transfusion',
    'cquirurgicas': 'quirurgicas',
    'ivcontrol': 'IV control',
    ' i v': 'IV',
    'iv': 'IV',
    'secrecione ': 'secreciones',
    'traqueostomia': 'traqueotomia',
    'control desintomas': 'control de sintomas',
    'contro d ': 'control de',
    'contrlol': 'control', 
    'ncontrol': 'control',
    'cantrol': 'control', 
    'controld': 'control',
    'controo': 'control',
    'contrl': 'control',
    'cntrl': 'control',
    'sintom': 'sintomas',
    'sintoms': 'sintomas',
    'sintpmas': 'sintomas',
    'simtomas': 'sintomas',
    'cadra': 'cadera',
    'couidados': 'cuidados',
    'palaitivos': 'paliativos',
    'paniativos': 'paliativos',
    'avanzadios': 'avanzados',
    'uirurgica': 'quirurgica',
    'valoracio ': 'valoracion',
    'valracion': 'valoracion',
    'vaoracion': 'valoracion',
    'valrar': 'valoracion',
    'diahgnostico': 'diagnostico',
    'infeccio': 'infeccion',
    'infec': 'infeccion',
    'trao': 'tratamiento',
    'trat ': 'tratamiento',
    'respirat ': 'respiratoria',
    'administacion': 'administracion',
    'adminiostracion':  'administracion',
    'antiibiotico': 'antibiotico',
    'd': 'de',
    'e': 'de'
}

# Buscar y reemplazar cada palabra en el DataFrame utilizando el diccionario
for word, replacement in replacement_dict_ing.items():
    df['motivo_ing'] = df['motivo_ing'].str.replace(r'\b{}\b'.format(word), replacement, case=False, regex=True)


In [94]:
# Buscamos palabras
words = ['  ']

# Convierte la lista de palabras en una expresión regular
regex = r'\b(?:{})\b'.format('|'.join(words))
df['motivo_ing'].str.contains(regex, case=False, regex=True).value_counts()

False    4012
True        1
Name: motivo_ing, dtype: int64

In [95]:
# Buscar filas que contienen la secuencia de espacios
contains_spaces = df['motivo_ing'].str.contains(regex, case=False, regex=True)

# Obtener los índices de estas filas
true_indices = df[contains_spaces].index
true_indices

Int64Index([2179], dtype='int64')

In [96]:
df['motivo_ing'][true_indices]

2179    curas  pulsos de metilprenisolona
Name: motivo_ing, dtype: object

In [97]:
df['motivo_ing'][true_indices] = df['motivo_ing'][true_indices].replace('\\s+', ' ', regex=True).str.strip()

[09/06/23 18:11:08] WARNING  C:\Users\Pablo                                                         warnings.py:109
                             Villar\AppData\Local\Temp\ipykernel_4476\1441226308.py:1:                             
                             SettingWithCopyWarning:                                                               
                             A value is trying to be set on a copy of a slice from a DataFrame                     
                                                                                                                   
                             See the caveats in the documentation:                                                 
                             https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#                
                             returning-a-view-versus-a-copy                                                        
                               df['motivo_ing'][true_indices] =                                                    
                             df['motivo_ing'][true_indices].replace('\\s+', ' ',                                   
                             regex=True).str.strip()                                                               
                                                                                                                   

In [98]:
# Buscamos palabras
words = ['  ']

# Convierte la lista de palabras en una expresión regular
regex = r'\b(?:{})\b'.format('|'.join(words))
df['motivo_ing'].str.contains(regex, case=False, regex=True).value_counts()

False    4013
Name: motivo_ing, dtype: int64

In [99]:
motivo_ing_lista = df['motivo_ing'].unique()
print(len(motivo_ing_lista),sorted(s_procedencia_lista, reverse=False))

570 ['acv', 'angiologia', 'anr', 'ap', 'cardiologia', 'cgd', 'cgdurg', 'cirugia cardiaca', 'cirugia cardiologia', 'cirugia general', 'cirugia maxilofacial', 'cirugia plastica', 'cirugia toracica', 'cirugia vascular', 'clp', 'consulta ela multidisciplinar', 'consulta hipertension', 'consulta mir', 'consultas externas cirugia plastica', 'consultas externas digestivo', 'consultas externas mir', 'consultas externas neumologia', 'consultas externas oncologia', 'consultas oncologia', 'cot', 'cpr', 'crg', 'der', 'diagestivo', 'digestivo', 'eif', 'eif mir', 'endocrinologia', 'enfermedad infecciosas', 'ginecologia', 'hado', 'hdd neumologia', 'hematologia', 'hematologia urgencias', 'hepatologia', 'hospital de dia', 'infecciosas', 'maxilofacial', 'medicina interna', 'mir', 'mir conxo', 'mir gil', 'mir gil casares no', 'mir infecciosas', 'mir p', 'mir p consultas externas', 'mir provincial', 'mirap protocolo hierro en domicilio', 'mirc', 'mireif', 'mirg', 'mirhp', 'mirlugo', 'ncr', 'nefrologia', '

In [78]:
df['motivo_ing'].value_counts()

control de sintomas                                                                                                      982
tratamiento antibiotico IV                                                                                               374
antibioterapia IV                                                                                                        345
control sintomas                                                                                                         221
valoracion                                                                                                               128
control evolutivo                                                                                                        106
continuacion de cuidados                                                                                                 102
cuidados paliativos                                                                                                       85


## 6.6. Replace motivo_alta

In [100]:
motivo_alta_lista = df['motivo_alta'].unique()
print(len(motivo_alta_lista),sorted(motivo_alta_lista, reverse=False))

99 ['alta paso a urgencias', 'alta paso por urgencias', 'alta por paso a uregncias', 'alta por paso a urgencias', 'buen control de sintomas', 'cambio de domicilio fuera de area asistencial de hado', 'claudicacion familiar', 'consulta medica', 'cuidados ap', 'derivado urgencias', 'desconocido', 'domicilio', 'estable en su enfermedad', 'exitus', 'exitus comunicado por la familia', 'fin cuidados', 'fin de cuidados', 'fin de cuidadso', 'imposibilidad de cuidados en domicilio del paciente por condiciones higienocosanitarias inadecuadas', 'ingreso cgd', 'ingreso cirugia vascular', 'ingreso en cplastica', 'ingreso en cvascular', 'ingreso en digestivo', 'ingreso en digestivo clinico', 'ingreso en huac para transplante pulmonar', 'ingreso en medicina interna', 'ingreso en mir', 'ingreso en nrc', 'ingreso en nrl', 'ingreso en oncologia', 'ingreso en orl', 'ingreso en upal', 'ingreso en utr', 'ingreso medicina interna', 'ingreso mir', 'ingreso nml clinico', 'ingreso onco', 'ingreso para trasplant

In [101]:
# Crear un diccionario de palabras a buscar y reemplazar
replacement_dict_alta = {
    'uregncias': 'urgencias',
    'urg': 'urgencias',
    'cuidadso': 'cuidados',
    'onco': 'oncologia',
    'onc': 'oncologia',
    'reingres': 'reingreso',
    'reingresoupal': 'reingreso upal',
    'tralado': 'traslado',
    'trasado': 'traslado',
    'tto': 'tratamiento'
}

# Buscar y reemplazar cada palabra en el DataFrame utilizando el diccionario
for word, replacement in replacement_dict_alta.items():
    df['motivo_alta'] = df['motivo_alta'].str.replace(r'\b{}\b'.format(word), replacement, case=False, regex=True)


In [102]:
motivo_alta_lista = df['motivo_alta'].unique()
print(len(motivo_alta_lista),sorted(motivo_alta_lista, reverse=False))

91 ['alta paso a urgencias', 'alta paso por urgencias', 'alta por paso a urgencias', 'buen control de sintomas', 'cambio de domicilio fuera de area asistencial de hado', 'claudicacion familiar', 'consulta medica', 'cuidados ap', 'derivado urgencias', 'desconocido', 'domicilio', 'estable en su enfermedad', 'exitus', 'exitus comunicado por la familia', 'fin cuidados', 'fin de cuidados', 'imposibilidad de cuidados en domicilio del paciente por condiciones higienocosanitarias inadecuadas', 'ingreso cgd', 'ingreso cirugia vascular', 'ingreso en cplastica', 'ingreso en cvascular', 'ingreso en digestivo', 'ingreso en digestivo clinico', 'ingreso en huac para transplante pulmonar', 'ingreso en medicina interna', 'ingreso en mir', 'ingreso en nrc', 'ingreso en nrl', 'ingreso en oncologia', 'ingreso en orl', 'ingreso en upal', 'ingreso en utr', 'ingreso medicina interna', 'ingreso mir', 'ingreso nml clinico', 'ingreso oncologia', 'ingreso para trasplante', 'ingreso upal', 'no', 'no fue dado de a

## 6.7. Replace medico

In [103]:
medico_lista = df['medico'].unique()
print(len(medico_lista),sorted(medico_lista, reverse=False))

17 ['200', 'beceiro', 'desconocido', 'fernandez benito', 'galego feal', 'gomez buela', 'ibanez alonso', 'lopez renedo', 'masa', 'masa vazquez', 'novo', 'pazo', 'suarez', 'suarez prado', 'valcarcel', 'valdes', 'villar del castillo']


In [104]:
df['medico'].str.replace("masa vazquez", "masa")
df['medico'].str.replace("suarez prado", "suarez")
df['medico'].str.replace("200", "desconocido")

0                    valdes
1               galego feal
2              lopez renedo
3              lopez renedo
4              lopez renedo
5       villar del castillo
6                 valcarcel
7              lopez renedo
8                    suarez
9                    suarez
10      villar del castillo
11      villar del castillo
12      villar del castillo
13      villar del castillo
14            ibanez alonso
15            ibanez alonso
16                   suarez
17                   suarez
18            ibanez alonso
19            ibanez alonso
20                   suarez
21                   suarez
22            ibanez alonso
23            ibanez alonso
24                   suarez
25                   suarez
26                   suarez
27                   suarez
28                   suarez
29                   suarez
30                   suarez
31                   suarez
32                   suarez
33             lopez renedo
34             lopez renedo
35            ibanez

In [105]:
# Crear un diccionario de palabras a buscar y reemplazar
replacement_dict_med = {
    '200': 'desconocido',
    'masa vazquez': 'masa',
    'suarez prado': 'suarez'
}

df['medico'] = df['medico'].astype(str)
df['medico'] = df['medico'].replace(replacement_dict_med, regex=True)

In [106]:
medico_lista = df['medico'].unique()
print(len(medico_lista),sorted(medico_lista, reverse=False))

14 ['beceiro', 'desconocido', 'fernandez benito', 'galego feal', 'gomez buela', 'ibanez alonso', 'lopez renedo', 'masa', 'novo', 'pazo', 'suarez', 'valcarcel', 'valdes', 'villar del castillo']


## 6.8. Replace sedacion

In [107]:
sed_lista = df['sedacion'].unique()
print(len(sed_lista),sorted(sed_lista, reverse=False))

35 ['00', 'desconocido', 'morfbuschalop', 'no', 'si', 'si buscap midazolam haloperidolmorfina', 'si buscap midazolam morfina', 'si buscap midazolam morfinasinogan', 'si buscap midazolammorfina', 'si buscapina midazolam morfina y haloperidol', 'si buscapina morfina', 'si buscapmidazmorf', 'si buscapmidazmorfhaloperidol', 'si levomepromazina midazolam buscapina morfina', 'si levomepromazina midazolam morfina', 'si midazmorfbuscap', 'si midazolam', 'si midazolam haloperidol buscapina morfina', 'si midazolam morfina buscapina', 'si midazolan', 'si morfina buscapina', 'si morfina haloperidol midazolam', 'si morfina levomepromazina midazolam buscapina', 'sibuscaphalopsinoganmorfmidaz', 'sibuscapmidazolammorfina', 'sibuscapsonogancl morfmidaz', 'sibuscmidmorfhalop', 'siclmorficomidazolam', 'simidazolam morfina buscapina', 'simidazolammorfinabuscapina', 'simidazolanmorhhaloperidol', 'simidmorfbuscap', 'simidzmorfhaloperidolbuscap', 'simorfbuscaphaloperidolmidaz', 'simorfbuscapmidaz']


In [108]:
#Valores: Buscapina, Morfina, Haloperidol, Midazolam, Levomepromazina

# Crear un diccionario de palabras a buscar y reemplazar
replacement_dict_sed = {
    'sibuscaphalopsinoganmorfmidaz': 'si buscapina haloperidol morfina',
    'simidzmorfhaloperidolbuscap': 'si midazolam morfina buscapina haloperidol buscapina',
    'simorfbuscaphaloperidolmidaz': 'si morfina buscapina haloperidol midazolam',
    'buscapmidazmorfhaloperidol': 'buscapina midazolam morfina haloperidol',
    'simidazolanmorhhaloperidol': 'si midazolam morfina haloperidol',
    'sibuscapmidazolammorfina': 'si buscapina midazolam morfina',
    'simidazolammorfinabuscapina': 'si midazolam morfina buscapina',
    'sibuscmidmorfhalop': 'si buscapina midazolam morfina haloperidol',
    'siclmorficomidazolam': 'si morfina midazolam',
    'morfbuschalop': 'si morfina buscapina haloperidol',
    'haloperidolmorfina': 'si haloperidol morfina',
    'sibuscapsonogancl': 'si buscapina morfina',
    'simorfbuscapmidaz': 'si morfina buscapina midazolam',
    'morfinasinogan': 'morfina',
    'simidmorfbuscap': 'si midazolam morfina buscapina',
    'simidazolam': 'si midazolam',
    'buscapmidazmorf': 'buscapina midazolam morfina',
    'midazolammorfina': 'midazolam morfina',
    'midazmorfbuscap': 'midazolam morfina buscapina',
    'buscap': 'buscapina',
    ' y ': ''
}

# Buscar y reemplazar cada palabra en el DataFrame utilizando el diccionario
for word, replacement in replacement_dict_sed.items():
    df['sedacion'] = df['sedacion'].str.replace(r'\b{}\b'.format(word), replacement, case=False, regex=True)


In [109]:
sed_lista = df['sedacion'].unique()
print(len(sed_lista),sorted(sed_lista, reverse=False))

26 ['00', 'desconocido', 'no', 'si', 'si buscapina haloperidol morfina', 'si buscapina midazolam morfina', 'si buscapina midazolam morfina haloperidol', 'si buscapina midazolam morfinahaloperidol', 'si buscapina midazolam si haloperidol morfina', 'si buscapina morfina', 'si buscapina morfina morfmidaz', 'si levomepromazina midazolam buscapina morfina', 'si levomepromazina midazolam morfina', 'si midazolam', 'si midazolam haloperidol buscapina morfina', 'si midazolam morfina buscapina', 'si midazolam morfina buscapina haloperidol buscapina', 'si midazolam morfina haloperidol', 'si midazolan', 'si morfina buscapina', 'si morfina buscapina haloperidol', 'si morfina buscapina haloperidol midazolam', 'si morfina buscapina midazolam', 'si morfina haloperidol midazolam', 'si morfina levomepromazina midazolam buscapina', 'si morfina midazolam']


## 6.9. Replace ayuntamiento

In [110]:
ayto_lista = df['ayuntamiento'].unique()
print(len(ayto_lista),sorted(ayto_lista, reverse=False))

44 ['a bana', 'a estrada', 'ames', 'boqueixon', 'brion', 'desconocido', 'dodro', 'estrada', 'frades', 'la estrada', 'lalin', 'losame', 'lousame', 'negreira', 'no pino', 'noia', 'noya', 'ordenes', 'ordes', 'oroso', 'ortono', 'padron', 'pontecesuras', 'pontecesures', 'pontevea', 'rianxo', 'rois', 'santa comba', 'santiago', 'santiago compostela', 'santiago de com', 'santiago de compostela', 'sigueiro', 'silleda', 'sionlla', 'teo', 'tordoia', 'tordoya', 'touro', 'trazo', 'val do dubra', 'valga', 'vedra', 'vila de cruces']


In [111]:
#Valores: Buscapina, Morfina, Haloperidol, Midazolam, Levomepromazina

# Crear un diccionario de palabras a buscar y reemplazar
replacement_dict_ayto = {
    'la estrada': 'estrada',
    'a estrada': 'estrada',
    'losame': 'lousame',
    'ordenes': 'ordes',
    'pontecesuras': 'pontecesures',
    'santiago compostela': 'santiago',
    'santiago de com': 'santiago',
    'santiago de compostela': 'santiago',
    'tordoya': 'tordoia',
    'noya': 'noia'
}

# Buscar y reemplazar cada palabra en el DataFrame utilizando el diccionario
for word, replacement in replacement_dict_ayto.items():
    df['ayuntamiento'] = df['ayuntamiento'].str.replace(r'\b{}\b'.format(word), replacement, case=False, regex=True)


In [112]:
ayto_lista = df['ayuntamiento'].unique()
print(len(ayto_lista),sorted(ayto_lista, reverse=False))

34 ['a bana', 'ames', 'boqueixon', 'brion', 'desconocido', 'dodro', 'estrada', 'frades', 'lalin', 'lousame', 'negreira', 'no pino', 'noia', 'ordes', 'oroso', 'ortono', 'padron', 'pontecesures', 'pontevea', 'rianxo', 'rois', 'santa comba', 'santiago', 'sigueiro', 'silleda', 'sionlla', 'teo', 'tordoia', 'touro', 'trazo', 'val do dubra', 'valga', 'vedra', 'vila de cruces']


## 6.10. Replace otros

In [114]:
otros_lista = df['otros'].unique()
print(len(otros_lista),sorted(otros_lista, reverse=False))

49 ['610', 'acv', 'c plastica', 'c vascular', 'cardiologia', 'carnefrocvasc', 'ccee', 'ce', 'cgd', 'consulta', 'consultas', 'dig', 'familia', 'familiares', 'hija', 'hla rosaleda', 'hospital la rosaleda', 'hospitales madrid', 'iniciativa propia', 'mir', 'mno', 'ncr', 'nef', 'nefro', 'nefro y dig', 'nml', 'nmlend', 'no', 'nol', 'nrl', 'onc', 'p la rosaleda', 'pac santiago', 'paliativos salnes', 'policlinico la rosaleda', 'privado', 'residencia', 'residencia san marcos', 'residencia sanitaria', 'residencia sociosanitaria as dores', 'rosaleda', 'rtp', 'si', 'solicitud familiar', 'unidad ef mir', 'urg', 'uro', 'uro cardiologia', 'vascular']


In [115]:
#Valores: Buscapina, Morfina, Haloperidol, Midazolam, Levomepromazina

# Crear un diccionario de palabras a buscar y reemplazar
replacement_dict_otros = {
    'ccee': 'consultas externas',
    'ce': 'consultas externas',
    'consulta': 'consultas',
    'familia': 'familiares',
    'hla rosaleda': 'rosaleda',
    'hospital la rosaleda': 'rosaleda',
    'p la rosaleda': 'rosaleda',
    'policlinico la rosaleda': 'rosaleda',
    'nef': 'nefrologia',
    'nefro': 'nefrologia',
    'dig': 'digestivo',
    'nml': 'neumologia',
    'nmlend': 'neumologia endocrino',
    'onc': 'oncologia',
    'urg': 'urgencias',
    'uro': 'urologia',
    
}

# Buscar y reemplazar cada palabra en el DataFrame utilizando el diccionario
for word, replacement in replacement_dict_otros.items():
    df['otros'] = df['otros'].str.replace(r'\b{}\b'.format(word), replacement, case=False, regex=True)


In [116]:
otros_lista = df['otros'].unique()
print(len(otros_lista),sorted(otros_lista, reverse=False))

41 ['610', 'acv', 'c plastica', 'c vascular', 'cardiologia', 'carnefrocvasc', 'cgd', 'consultas', 'consultas externas', 'digestivo', 'familiares', 'hija', 'hospitales madrid', 'iniciativa propia', 'mir', 'mno', 'ncr', 'nefrologia', 'nefrologia y digestivo', 'neumologia', 'neumologia endocrino', 'no', 'nol', 'nrl', 'oncologia', 'pac santiago', 'paliativos salnes', 'privado', 'residencia', 'residencia san marcos', 'residencia sanitaria', 'residencia sociosanitaria as dores', 'rosaleda', 'rtp', 'si', 'solicitud familiar', 'unidad ef mir', 'urgencias', 'urologia', 'urologia cardiologia', 'vascular']


## 6.11. Replace otros_1

In [117]:
otros_1_lista = df['otros_1'].unique()
print(len(otros_1_lista),sorted(otros_1_lista, reverse=False))

173 ['0clusion intestinal', 'abdomen agudo', 'acv previo', 'agitacion', 'agitacionpanico', 'agitacioondiarrea', 'agonia', 'agresividad', 'anemia', 'angustia', 'animo depresivo', 'ansiedad', 'ansiedadinsomnio', 'anuria', 'ascitis', 'ascitisictericia', 'bajo nivel conciencia', 'broncoaspiracion', 'ca colon', 'ca gastrico', 'candidiasis', 'candidiasis oral', 'candidiasis orof', 'coma', 'coma profundo', 'comatosa', 'declive severo', 'demencia', 'depresion reactiva', 'derrame pleural', 'deterior del nivel de consciencia', 'deterioro cognitivo', 'deterioro estado generalmelenas', 'deterioro funcional', 'diabetes', 'diarrea', 'diarreadeshidratacion', 'dificultad ingesta oral', 'disfagia', 'dispepsia', 'dispepsia por metronidazol oral', 'disuria y polaquiuria', 'dolo roseo', 'dolor', 'dolor abdominal', 'dolor epigastrico', 'edema lengua', 'edema minf', 'edema minferiores', 'edemas', 'edemas oliguria', 'encefalopatia ascitis insuficiencia renal', 'esclerosis m', 'espondilodiscitis', 'estrenimie

In [118]:
#Valores: Buscapina, Morfina, Haloperidol, Midazolam, Levomepromazina

# Crear un diccionario de palabras a buscar y reemplazar
replacement_dict_otros_1 = {
    '0clusion intestinal': 'oclusion intestinal',
    'agitacionpanico': 'agitacion panico',
    'agitacioondiarrea': 'agitacion diarrea',
    'ansiedadinsomnio': 'ansiedad insomnio',
    'ascitisictericia': 'ascitis ictericia',
    'deterior': 'deterioro',
    'diarreadeshidratacion': 'diarrea deshidratacion',
    'policlinico la rosaleda': 'rosaleda',
    'mareo': 'mareos',
    'n no': 'no',
    'nauseasvomitos': 'nauseas y vomitos',
    'si vomitos': 'vomitos',
    'sinauseas': 'nauseas',
    'siretencion': 'retencion',
    'sivomitoshematemesis': 'vomitos hematemesis',
    'tosexpectoracion': 'tos y expectoracion',
    'ulceras de presion': 'ulceras presion',
    'vomitosestrenimiento': 'vomitos estrenimiento',
    'ni': 'si',
    'perdida d ela via oral': 'perdida de via oral',
    'perdida de la via oral': 'perdida de via oral',
    'sconfusional': 'sindrome confusional',
    'sd confusional': 'sindrome confusional',
    'vomito': 'vomitos',
    
}

# Buscar y reemplazar cada palabra en el DataFrame utilizando el diccionario
for word, replacement in replacement_dict_otros_1.items():
    df['otros_1'] = df['otros_1'].str.replace(r'\b{}\b'.format(word), replacement, case=False, regex=True)


In [119]:
otros_1_lista = df['otros_1'].unique()
print(len(otros_1_lista),sorted(otros_1_lista, reverse=False))

162 ['abdomen agudo', 'acv previo', 'agitacion', 'agitacion diarrea', 'agitacion panico', 'agonia', 'agresividad', 'anemia', 'angustia', 'animo depresivo', 'ansiedad', 'ansiedad insomnio', 'anuria', 'ascitis', 'ascitis ictericia', 'bajo nivel conciencia', 'broncoaspiracion', 'ca colon', 'ca gastrico', 'candidiasis', 'candidiasis oral', 'candidiasis orof', 'coma', 'coma profundo', 'comatosa', 'declive severo', 'demencia', 'depresion reactiva', 'derrame pleural', 'deterioro cognitivo', 'deterioro del nivel de consciencia', 'deterioro estado generalmelenas', 'deterioro funcional', 'diabetes', 'diarrea', 'diarrea deshidratacion', 'dificultad ingesta oral', 'disfagia', 'dispepsia', 'dispepsia por metronidazol oral', 'disuria y polaquiuria', 'dolo roseo', 'dolor', 'dolor abdominal', 'dolor epigastrico', 'edema lengua', 'edema minf', 'edema minferiores', 'edemas', 'edemas oliguria', 'encefalopatia ascitis insuficiencia renal', 'esclerosis m', 'espondilodiscitis', 'estrenimiento', 'estrenimien

## 6.12. Replace otros_complicaciones

In [120]:
otros_complicaciones_lista = df['otros_complicaciones'].unique()
print(len(otros_complicaciones_lista),sorted(otros_complicaciones_lista, reverse=False))

414 ['abdomen agudo', 'abdomen agudoneumonia', 'absceso facial', 'absceso pared abdominal', 'absceso pelvicofistula intestinalsde compartimental muslo dcho', 'acv', 'adenocarcinoma pancreas estadio iv', 'agitacion', 'agitacion e insomnio', 'agitacion psicomotriz', 'agonia', 'alergia aminoglucosidos', 'alteracion enzimas hepaticas', 'anemia', 'anemizacion', 'angustia disnea secreciones', 'angustia perdida de la via oral', 'ansiedad', 'artritis celulitis vomitos', 'ascitis no a tension', 'asistolia', 'astenia', 'ausencia de cuidador por limitacion intervencio social', 'broncoaspiracion', 'broncoaspiraciones', 'bypass axilo monofemoral desde arteria axilar izquierda 1aporcion lt hasta arteria femoral profunda izquierda tl miembro inferior izquierdo', 'candidiasis', 'candidiasis oral', 'candidiasis orofaringe', 'candidiasis orofaringea', 'candidiasis orofingea', 'cardiopatia hipertensiva fa', 'celilitis', 'celulitis', 'claud familiar domicilio', 'claudicacion', 'claudicacion familiar', 'cl

In [121]:
#Valores: Buscapina, Morfina, Haloperidol, Midazolam, Levomepromazina

# Crear un diccionario de palabras a buscar y reemplazar
replacement_dict_otros_complicaciones = {
    'celilitis': 'celulitis',
    'agudoneumonia': 'agudo neumonia',
    'claud': 'claudicacion',
    'situacionultimosdias': 'situacion ultimos dias',
    'cura': 'curas',
    'diarreaestrenimientodiabetes': 'diarrea estrenimiento diabetes',
    'dipepsiaalteracion': 'dispepsia alteracion',
    'disna': 'disnea',
    'insuficiencia resp aguda': 'insuficiencia respiratoria aguda',
    'inf respiratoria': 'infeccion respiratoria',
    'infecc respiratoria': 'infeccion respiratoria',
    'ifec respirat': 'infeccion respiratoria',
    'broncoaspiraciondiarrea': 'broncoaspiracion diarrea',
    'hematuriacancer': 'hematuria cancer',
    'hiperglucemiaicc': 'hiperglucemia icc',
    'htadiabetes': 'hta diabetes',
    'i cardiaca irenal cr': 'insuficiencia cardiaca insuficiencia renal cronica',
    'icc': 'insuficiencia cardiaca cronica',
    'inquietudinsomnio': 'inquietud insomnio',
    'nauseasvomitos': 'nauseas y vomitos',
    'nuseas': 'nauseas',
    'intestinalclaudicacion': 'intestinal claudicacion',
    'insuf': 'insuficiencia',
    'sde confusional': 'sindrome confusional',
    'sd confusional': 'sindrome confusional',
    'sconfusional': 'sindrome confusional',
    'si ': '', # modifico todos los 'si ' con espacio por nada, ya que se entiende que presenta sintomas, enfermedades, ttos, etc.
    'siclaudicacion': 'claudicacion',
    'sibroncoaspiracion': 'broncoaspiracion',
    'siagitacion': 'agitacion',
    'siacv': 'acv',
    'sicaida': 'caida',
    'sicovid': 'covid',
    'sideterioro': 'deterioro',
    'sidisnea': 'disnea',
    'sidolor': 'dolor',
    'sifallo': 'fallo',
    'sifracaso': 'fracaso',
    'siinsuficiencia': 'insuficiencia',
    'siisquemia': 'isquemia',
    'sihemorragia': 'hemorragia',
    'siinfecciones': 'infecciones',
    'siinfeccion': 'infeccion',
    'sinauseas': 'nauseas',
    'sioclusion': 'oclusion',
    'vomitosestrenimiento': 'vomitos estrenimiento',
    'siparada': 'parada',
    'sirectorragias': 'rectorragias',
    'sirectorragia': 'rectorragia',
    'sisangrado': 'sangrado',
    'digestivoitu': 'digestivo itu',
    'sisepsis': 'sepsis',
    'sivomitos': 'vomitos',
    'ucera': 'ulcera',
    'ulceras de presion': 'ulceras presion',
    'ulceras por presion': 'ulceras presion',
}

# Buscar y reemplazar cada palabra en el DataFrame utilizando el diccionario
for word, replacement in replacement_dict_otros_complicaciones.items():
    df['otros_complicaciones'] = df['otros_complicaciones'].str.replace(r'\b{}\b'.format(word), replacement, case=False, regex=True)


In [122]:
otros_complicaciones_lista = df['otros_complicaciones'].unique()
print(len(otros_complicaciones_lista),sorted(otros_complicaciones_lista, reverse=False))

372 ['abdomen agudo', 'abdomen agudo neumonia', 'absceso facial', 'absceso pared abdominal', 'absceso pelvicofistula intestinalsde compartimental muslo dcho', 'acv', 'adenocarcinoma pancreas estadio iv', 'agitacion', 'agitacion e insomnio', 'agitacion psicomotriz', 'agonia', 'alergia aminoglucosidos', 'alteracion enzimas hepaticas', 'alucinosis', 'anemia', 'anemizacion', 'angustia disnea secreciones', 'angustia perdida de la via oral', 'ansiedad', 'artritis celulitis vomitos', 'artritis por microcristales', 'ascitis hdb pbe encefalopatia', 'ascitis no a tension', 'asistolia', 'astenia', 'ausencia de cuidador por limitacion intervencio social', 'broncoaspiracion', 'broncoaspiraciones', 'bypass axilo monofemoral desde arteria axilar izquierda 1aporcion lt hasta arteria femoral profunda izquierda tl miembro inferior izquierdo', 'caida', 'candidiasis', 'candidiasis oral', 'candidiasis orofaringe', 'candidiasis orofaringea', 'candidiasis orofingea', 'cardiopatia hipertensiva fa', 'celulitis

## 6.13. Fecha alta

Para la columna fecha de alta la pasaremos a formato `datetime`

In [123]:
df['fecha_alta'] = df['fecha_alta'].str.replace('t', '')

In [124]:
df['fecha_alta'] = pd.to_datetime(df['fecha_alta'], format='%Y%m%d%H%M%S', errors='coerce')

In [125]:
df['fecha_alta'] = df['fecha_alta'].dt.date

In [126]:
df['fecha_alta'] = pd.to_datetime(df['fecha_alta'])
df['fecha_alta'] = df['fecha_alta'].dt.strftime('%d/%m/%Y')

In [127]:
df['fecha_alta'].isna().sum()

3253

In [128]:
df['fecha_alta'] = df['fecha_alta'].fillna('')

## 6.14. Numéricos [ps_ecog, barthel, gds_fast, eva_ing]

In [129]:
df[
    ['fe_iv', 
    'toracocentesis', 
    'paracentesis', 
    'transfusion',
    'trato_antibiotico',
    'cronico_reag',
    'agudo_estable',
    'ast_anorx',
    'agonia',
    'p_terminal',
    'delirium',
    'dolor',
    'disnea',
    'fiebre',
    'paliativo_no_onc_noc',
    'paliativo_onc_noc',
    'ap'   
   ]
  ] = df[
    ['fe_iv', 
    'toracocentesis', 
    'paracentesis', 
    'transfusion',
    'trato_antibiotico',
    'cronico_reag',
    'agudo_estable',
    'ast_anorx',
    'agonia',
    'p_terminal',
    'delirium',
    'dolor',
    'disnea',
    'fiebre',
    'paliativo_no_onc_noc',
    'paliativo_onc_noc',
    'ap'   
   ]
  ].fillna('')

# 7. Sedacion si tiene o no tiene y tipos de medicamentos

* Separamos las palabras en una lista con los medicamentos y en base a si los contiene crearemos nuevas columnas

In [128]:
# Cargo un nuevo df limpio de Kedro

df = catalog.load("hado_cleaned")

[08/11/23 10:41:10] INFO     Loading data from 'hado_cleaned' (CSVDataSet)...                   data_catalog.py:345

In [130]:
df['tiene_sedacion'] = df['sedacion'].apply(lambda x: 0 if x == 'no' or x == '00' else 1)

In [131]:
df['tiene_sedacion'].value_counts()

0    3321
1     692
Name: tiene_sedacion, dtype: int64

In [132]:
# Lista de medicamentos
medicamentos = ['morfina', 'midazolam', 'buscapina', 'haloperidol', 'levomepromazina']

for medicamento in medicamentos:
    df[medicamento] = df['sedacion'].apply(lambda x: 1 if medicamento in x else 0)

In [133]:
for col in df[medicamentos]:
    print(df[col].value_counts())

0    3940
1      73
Name: morfina, dtype: int64
0    3944
1      69
Name: midazolam, dtype: int64
0    3944
1      69
Name: buscapina, dtype: int64
0    4002
1      11
Name: haloperidol, dtype: int64
0    4006
1       7
Name: levomepromazina, dtype: int64


In [135]:
df.columns

Index(['h_procedencia', 's_procedencia', 'ap', 'otros', 'diagnostico',
       'motivo_ing', 'paliativo_onc_noc', 'paliativo_no_onc_noc', 'fiebre',
       'disnea', 'dolor', 'delirium', 'otros_1', 'p_terminal', 'agonia',
       'ps_ecog', 'barthel', 'gds_fast', 'eva_ing', 'otros_2',
       'otros_complicaciones', 'n_estancias', 'n_visitas', 'sedacion',
       'motivo_alta', 'medico', 'year', 'ast_anorx', 'agudo_estable',
       'cronico_reag', 'trato_antibiotico', 'transfusion', 'paracentesis',
       'toracocentesis', 'ayuntamiento', 'fecha_alta', 'fe_iv',
       'tiene_sedacion', 'morfina', 'midazolam', 'buscapina', 'haloperidol',
       'levomepromazina'],
      dtype='object')

In [121]:
# Guardar una copia en csv de los datos limpios en data

df.to_csv(path_or_buf= "../data/02_intermediate/HADO_clean.csv", sep="^", index=False)

In [136]:
# Guardo los diagnosticos en un txt para verlos todos

# Obtener los valores únicos de la columna 'diagnostico'
resultados = df['diagnostico'].unique()

# Crear un DataFrame a partir de los resultados
df_resultados = pd.DataFrame(resultados, columns=['diagnostico'])

# Guardar el DataFrame en un archivo de texto
df_resultados.to_csv('resultados_diagnostico.txt', index=False)

# 8. Notas

Como hemos ido realizando el proyecto en Kedro este notebook se ha ido iterando con el tiempo y simplificándose

Puedo decir que el proceso de data cleaning y preprocessing se realiza una y otra vez a lo largo del proyecto, siempre surgen nuevos datos que no estaban contemplados en un primer momento. Al final estamos en un continuo proceso de limpieza y mantenimiento hasta que finaliza el proyecto y dejan de aportarse datos.

<hr>
<hr>

# METER EN OTRO NOTEBOOK A PARTIR DE AQUÍ

In [123]:
df_resultados.sample(150).to_csv('resultados_sample.txt', index=False)

Una vez realizada la limpieza y preprocesamiento
## Hacemos la vectorización de texto

La vectorización de texto es el proceso de convertir palabras en vectores numéricos que pueden ser entendidos y procesados por un algoritmo de machine learning. Existen diferentes técnicas para hacer esto, entre las que se incluyen Bag of Words, TF-IDF, y Word2Vec.

>Word2Vec es un método que utiliza redes neuronales para aprender representaciones vectoriales de palabras a partir de un corpus de texto. Este método tiene la ventaja de que puede capturar el significado semántico de las palabras.

Tenemos que convertir los diagnosticos en una lista de listas haciendo un split de la variable 
```python
diagnosticos = df['diagnosticos'].unique()`
```

In [120]:
# Cargamos las stopwords

import nltk
from nltk.corpus import stopwords

# Descargar las stopwords de NLTK
nltk.download('stopwords')

# Obtener las stopwords en español
stopwords_es = stopwords.words('spanish')

# Aplicar la eliminación de stopwords a tu columna de texto
df['diagnostico'] = df['diagnostico'].apply(lambda x: ' '.join([word for word in x.split()\
                                                                if word not in (stopwords_es)]))


[nltk_data] Downloading package stopwords to C:\Users\Pablo
[nltk_data]     Villar\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [121]:
diagnosticos = df['diagnostico'].unique()
diagnosticos_split = [diagnostico.split() for diagnostico in diagnosticos]

In [122]:
diagnosticos_split

[['cancer', 'orl'],
 ['melanoma', 'vulvar'],
 ['cancer', 'broncogenico'],
 ['cirrosis', 'hepatica'],
 ['neplasia', 'mama', 'estadio', 'IV'],
 ['anemia'],
 ['adenoca', 'pulmon'],
 ['leucemia', 'linfatica', 'cronica'],
 ['fx', 'meseta', 'tibial'],
 ['cancer', 'mama'],
 ['cancer', 'prostata'],
 ['deterioro', 'general'],
 ['tumor', 'cerebral'],
 ['adenoca', 'colon', 'IV'],
 ['cancer', 'colon'],
 ['neumonia'],
 ['niemannpick'],
 ['sarcoidosis'],
 ['cancer', 'pancreas'],
 ['infeccion', 'urinaria', 'fallo', 'cardiaco'],
 ['melanoma', 'fosa', 'nasal'],
 ['cancer', 'timo'],
 ['infeccion', 'respiratoria'],
 ['sdown'],
 ['bocio', 'intratoracico'],
 ['sepsisi', 'respiratoria'],
 ['intolerancia', 'oral'],
 ['infeccion', 'urinaria'],
 ['esclerosis', 'multiple'],
 ['demencia', 'fallo', 'multiorganico'],
 ['cancer', 'parotida'],
 ['ITU', '(infeccion', 'tracto', 'urinario)'],
 ['ulceras', 'mmii'],
 ['smd'],
 ['cancer', 'colon', 'estadio', 'IV'],
 ['fractura', 'cadera'],
 ['fallo', 'cardiaco'],
 ['cance

In [123]:
from gensim.models import Word2Vec

# Asumiendo que tus diagnósticos ya están preprocesados y almacenados en una lista de listas,
# donde cada lista interna contiene las palabras de un diagnóstico.
# Por ejemplo: [["neoplasia", "pancreas"], ["adenocarcinoma", "de", "pulmón"], ...]

# Entrenamos el modelo Word2Vec
model = Word2Vec(diagnosticos_split, min_count=1, vector_size=50)

# Ahora podemos obtener el vector de una palabra en particular
vector = model.wv['cancer']

# O incluso obtener la palabra más similar a 'cancer'
similar = model.wv.most_similar('cancer')


In [124]:
vector

array([-0.00059652,  0.00052158,  0.01040444,  0.01960699, -0.01930834,
       -0.01782835,  0.01624978,  0.02377817, -0.01329277, -0.00915849,
        0.0150449 , -0.00675792, -0.00875667,  0.01406383, -0.01399724,
       -0.00316409,  0.00747885,  0.00245794, -0.02084139, -0.02306509,
        0.0167302 ,  0.01300388,  0.01950894, -0.00136382,  0.01689705,
       -0.00717178, -0.00369646,  0.01144311, -0.01979169, -0.00762602,
       -0.0137384 , -0.00280863,  0.01857205, -0.0136458 , -0.00803991,
       -0.00228907,  0.01822545, -0.01289072,  0.00048408, -0.01278737,
       -0.01683586,  0.01039587, -0.01972936, -0.00783317,  0.00651448,
        0.00119866, -0.01783084,  0.01660989,  0.0131074 ,  0.0200562 ],
      dtype=float32)

In [125]:
similar

[('secuelas', 0.5250375270843506),
 ('sien', 0.45964503288269043),
 ('llc', 0.40486276149749756),
 ('asintomatica', 0.3927736282348633),
 ('varicosaobesidad', 0.37621062994003296),
 ('trombopenia', 0.3689652979373932),
 ('probable', 0.3682882785797119),
 ('paciente', 0.35990747809410095),
 ('demencia', 0.35750800371170044),
 ('patologica', 0.35407063364982605)]

### En el código anterior, min_count es el número mínimo de veces que una palabra debe aparecer en el corpus para ser incluida en el modelo, y vector_size es la dimensión de los vectores de palabra.

Word2Vec(diagnosticos_split, min_count=1, vector_size=50): Estás entrenando un modelo Word2Vec con tus diagnósticos. La opción min_count=1 significa que las palabras que aparecen al menos una vez en tus diagnósticos serán consideradas por el modelo, y vector_size=50 define la dimensionalidad de los vectores de palabras generados por el modelo.

model.wv['cancer']: Esto te devuelve el vector de la palabra 'cancer'. Este vector es un arreglo de 50 números (porque has definido vector_size=50) que representa el significado de 'cancer' según lo aprendido por el modelo de tus diagnósticos.

model.wv.most_similar('cancer'): Esto te devuelve las palabras más similares a 'cancer' según lo aprendido por el modelo de tus diagnósticos. La similitud se mide en términos de la similitud del coseno entre los vectores de palabras.

Por favor, ten en cuenta que el modelo Word2Vec necesita una gran cantidad de datos para aprender representaciones de palabras significativas. Si solo tienes un pequeño número de diagnósticos, los vectores de palabras generados por el modelo podrían no ser muy significativos. En este caso, puedes considerar el uso de vectores de palabras pre-entrenados, como los disponibles en bibliotecas como spaCy o gensim.

In [126]:
# Filtramos los diagnósticos vacíos
diagnosticos_split = [diagnostico for diagnostico in diagnosticos_split if diagnostico]

# Luego, volvemos a calcular los vectores de diagnósticos
diagnosticos_vec = [np.mean([model.wv[word] for word in diagnostico if word in model.wv.key_to_index], axis=0) for diagnostico in diagnosticos_split]

In [128]:
from sklearn.cluster import KMeans

# Primero, necesitamos convertir nuestros diagnósticos a vectores.
# Podemos hacer esto promediando los vectores de todas las palabras en cada diagnóstico.
diagnosticos_vec = [np.mean([model.wv[word] for word in diagnostico], axis=0) for diagnostico in diagnosticos_split]

# Entonces podemos entrenar un modelo KMeans en estos vectores.
kmeans = KMeans(n_clusters=5)  # Ajusta este número a la cantidad de grupos que creas adecuada
kmeans.fit(diagnosticos_vec)

# Ahora podemos obtener las etiquetas de los grupos para cada diagnóstico
labels = kmeans.labels_

                    WARNING  C:\Users\Pablo Villar\Desktop\CURSOS\KSchool\Máster en Data            warnings.py:109
                             Science\TFM\nuevo_entorno_kedro\lib\site-packages\sklearn\cluster\_kme                
                             ans.py:870: FutureWarning: The default value of `n_init` will change                  
                             from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to                     
                             suppress the warning                                                                  
                               warnings.warn(                                                                      
                                                                                                                   

In [129]:
labels

array([1, 2, 1, ..., 0, 3, 3])

In [130]:
# Crea un diccionario donde las llaves son las etiquetas del cluster y los valores son listas de diagnósticos pertenecientes a ese cluster
clusters = {i: [] for i in range(5)}  # Asegúrate de cambiar el rango para que coincida con el número de clusters que estás usando

for diagnostico, label in zip(diagnosticos_split, labels):
    clusters[label].append(' '.join(diagnostico))

# Ahora puedes imprimir los diagnósticos en cada cluster
for label, diagnosticos in clusters.items():
    print(f'Cluster {label}:')
    for diagnostico in diagnosticos:
        print(f'  {diagnostico}')


Cluster 0:
  leucemia linfatica cronica
  deterioro general
  niemannpick
  sepsisi respiratoria
  esclerosis multiple
  ITU (infeccion tracto urinario)
  amputacion
  deterioro cognitivo
  sindrome general
  masa abdominal
  hepatopatia cronica
  fa valvulopatia aortica insuficiencia cardiaca
  ITU (infeccion tracto urinario) asintomatica
  amputacion transmetatarsiana
  tratamiento antibiotico IV
  insuficiencia cardiaca
  broncoaspiracion
  linfoma hodking
  deterioro general trastorno metabolico
  linfoma bajo grado
  anoxia cerebral
  sindrome mielodisplasico
  deterioro cognitivo neumonia
  talasemiasindrome anemico
  neoplasia rectosepsi urinaria
  insuficiencia cardiaca descompensada
  deterioro cognitivo avanzado
  arteriopatia obliterante generalizada
  neoplasia renal metastasis hepaticas pulmonares
  neoplasia pancreas
  neoplasia pulmonar cirrosis
  neoplasia rectoacvborncoaspiraciono
  insuficiencia cardiaca llc atipica
  sde mielodisplasico
  neumonia deterioro cognitivo

In [131]:
for diagnostico, label in zip(diagnosticos_split, labels):
    clusters[label].append(' '.join(diagnostico))
    
    '''Está iterando sobre los diagnósticos y sus etiquetas de cluster correspondientes. 
    Para cada diagnóstico, transforma la lista de palabras en una cadena de texto (usando ' '.join(diagnostico)) 
    y la añade a la lista correspondiente en el diccionario clusters.
    
    Por ejemplo, si hay un diagnóstico que es ["neoplasia", "pancreas"] y su etiqueta de cluster es 2,
    este diagnóstico se transformaría en la cadena de texto "neoplasia pancreas" y se añadiría a la lista de diagnósticos
    del cluster 2 en el diccionario clusters. Así, al final, se crea un diccionario donde para cada cluster, 
    existe una lista de todos los diagnósticos (como cadenas de texto) que pertenecen a ese cluster'''

También puedes querer investigar las palabras más representativas de cada cluster. Esto puede darte una idea de las características que el modelo está utilizando para distinguir entre los diferentes clusters.
* Código de ejemplo para hacer eso:

In [132]:
import collections
# Para cada cluster, encuentra las 10 palabras más comunes
for label, diagnosticos in clusters.items():
    # Juntamos todos los diagnósticos en una sola lista de palabras
    palabras = [palabra for diagnostico in diagnosticos for palabra in diagnostico.split()]
    
    # Contamos las ocurrencias de cada palabra
    conteo_palabras = collections.Counter(palabras)
    
    print(f'Cluster {label}:')
    for palabra, conteo in conteo_palabras.most_common(10):
        print(f'  {palabra}: {conteo}')


Cluster 0:
  insuficiencia: 134
  cardiaca: 96
  cronica: 90
  neoplasia: 88
  (infeccion: 80
  tracto: 80
  urinario): 80
  ITU: 78
  cognitivo: 72
  deterioro: 64
Cluster 1:
  cancer: 290
  epidermoide: 28
  pulmon: 24
  colon: 22
  prostata: 16
  gastrico: 16
  recto: 16
  IV: 14
  vejiga: 10
  pancreas: 8
Cluster 2:
  ulceras: 66
  ulcera: 52
  carcinoma: 48
  absceso: 26
  neumonia: 22
  pie: 20
  eeii: 20
  obliteracion: 18
  grado: 18
  anemia: 16
Cluster 3:
  infeccion: 162
  respiratoria: 52
  demencia: 46
  urinaria: 34
  fragil: 34
  epoc: 32
  cirrosis: 24
  avanzada: 24
  celulitis: 24
  masa: 22
Cluster 4:
  IV: 252
  estadio: 248
  cancer: 88
  pulmon: 34
  neoplasia: 34
  colon: 30
  adenocarcinoma: 28
  neo: 22
  prostata: 16
  mama: 14


* El Cluster 0 parece incluir diagnósticos relacionados con úlceras, cáncer, EPOC, cirrosis, demencia y abscesos.

* El Cluster 1 parece estar más centrado en el cáncer, con palabras clave como carcinoma, colon, pulmón, páncreas y próstata.

* El Cluster 2 tiene un enfoque en infecciones, enfermedades respiratorias y úlceras.

* El Cluster 3 parece incluir diagnósticos que mencionan estadios (probablemente de cáncer) y diversas condiciones específicas como el cáncer de colon y el adenocarcinoma de pulmón.

* El Cluster 4 parece estar relacionado con el deterioro cognitivo, infecciones del tracto urinario (ITU), y también menciona el cáncer y la neoplasia.

>Estos clusters pueden ser útiles para entender qué tipos de diagnósticos se agrupan juntos y podrían ayudar en tareas como el análisis de datos, la recomendación de tratamientos, o la identificación de patrones en los diagnósticos.

- Es importante recordar que estos clusters se basan en la similitud de las palabras en los diagnósticos, que no necesariamente reflejan la similitud en las condiciones médicas que representan. Por lo tanto, cualquier interpretación o aplicación de estos clusters debe hacerse con cuidado y, preferiblemente, con la validación de un experto médico.

#  Técnicas de procesamiento de lenguaje natural (NLP) para agrupar diagnósticos similares

<hr>

# Otros

## Transformación diagnosticos

### 1.Corrección ortográfica: 
Usar bibliotecas como pyspellchecker para la corrección ortográfica. Sin embargo, este proceso puede ser computacionalmente costoso y no siempre proporciona resultados perfectos, ya que la corrección ortográfica puede ser un problema muy complejo. 

Otro enfoque podría ser construir un diccionario de correcciones comunes específicas para el conjunto de datos y aplicar estas correcciones de forma manual.

### 2.Procesamiento en lotes: 
En lugar de procesar el texto de cada fila de forma individual, puedes utilizar nlp.pipe(), que es una función de SpaCy que permite procesar textos en lotes. Esto puede ser mucho más eficiente que procesar cada texto de forma individual. 
> Pero queda descartado porque haré las correcciones de forma manual

### 3.Paralelización: 
Si estás utilizando una máquina con varios núcleos de CPU, puedes paralelizar el procesamiento para hacer un uso más eficiente de tus recursos computacionales. SpaCy tiene soporte para procesamiento paralelo a través de la función nlp.pipe(), simplemente estableciendo el argumento n_process a un número mayor que 1.

### 4.Clasificación de texto: 
Una vez corregidos los errores ortográficos. Se pasa a usar técnicas de aprendizaje automático para clasificar los diagnósticos en categorías. SpaCy tiene un componente de clasificación de texto con el que puedes entrenar los datos. Alternativamente, podrían usarse otras bibliotecas de aprendizaje automático, como scikit-learn, para construir un modelo de clasificación de texto.
> Utilizaré scikit-learn

### 5.Reducción de dimensionalidad: 
Algunas técnicas, como TF-IDF o word embeddings (por ejemplo, Word2Vec, FastText o las incrustaciones de palabras de SpaCy), pueden ayudarte a reducir la dimensionalidad de los datos de texto y a extraer características útiles para la clasificación.

### 6.Entrenamiento incremental: 
Si los datos están creciendo con el tiempo, puede considerarse el uso de un modelo que permita el entrenamiento incremental, es decir, un modelo que pueda ser actualizado con nuevos datos sin tener que ser reentrenado desde cero. Algunos modelos de SpaCy admiten esto, al igual que algunos modelos en bibliotecas como scikit-learn.

In [143]:
# Hacemos un sample
df_sample = df.sample(300)

In [144]:
df_sample.shape

(300, 37)

In [145]:
df_sample.head()

h_procedencia s_procedencia  ap otros                        diagnostico  \
3682       clinico     urgencias  no    no               hemorragia digestiva   
3223       clinico     urgencias  no    no   sde febril origen biliarurinario   
1851       clinico           mir  no    no    bacteriemia ir cr cancer pulmon   
3265            no           ncr  si    no  paralisis supranuclear progresiva   
315             no          upal  no    no                         cancer orl   

                      motivo_ing paliativo_onc_noc paliativo_no_onc_noc  \
3682           antibioterapia IV                si                   si   
3223           antibioterapia IV                no                   no   
1851  tratamiento antibiotico IV                si                   no   
3265         control de sintomas                no                   si   
315          control de sintomas                si                   no   

     fiebre disnea dolor delirium otros_1 p_terminal agonia ps_ecog barthel  \
3682     si     no    no       no      no      vacio  vacio      40      20   
3223     si     no    no       no      no      vacio  vacio      no      60   
1851     no     no    no       no      no      vacio     no      20      no   
3265     no     no    no       no      no      vacio  vacio      34      00   
315      no     no    si       si      no         si     si      40      20   

     gds_fast eva_ing      otros_2 otros_complicaciones  n_estancias  \
3682       70     NaN  desconocido                   no           40   
3223       no     NaN  desconocido                   no            9   
1851       no     NaN  desconocido                   no           11   
3265       7c     NaN  desconocido                   no            4   
315        no      no           no                   no            8   

      n_visitas                        sedacion           motivo_alta  \
3682         16                              no  traslado a urgencias   
3223          6                              no       fin de cuidados   
1851          5                              no       fin de cuidados   
3265          3                              si                exitus   
315           6  si buscapina midazolam morfina                exitus   

                   medico  year ast_anorx agudo_estable cronico_reag  \
3682               suarez  2022        no            no           si   
3223          galego feal  2022        si            no           si   
1851          galego feal  2020        si            no           no   
3265          gomez buela  2022        no            no           no   
315   villar del castillo  2017        si         vacio        vacio   

     trato_antibiotico transfusion paracentesis toracocentesis ayuntamiento  \
3682                si          no           no             no          teo   
3223                si          no           no             no         ames   
1851                si          no           no             no      no pino   
3265                no          no           no             no     santiago   
315              vacio       vacio        vacio          vacio  desconocido   

      fecha_alta  fe_iv  
3682  20/09/2022     no  
3223  27/06/2022     no  
1851              vacio  
3265  18/08/2022     no  
315               vacio

# TextBlob

* Corregir errores ortográficos (usando la biblioteca TextBlob para corrección automática):

>OJO no puede tener valores NA o de otro tipo que no sea object

In [146]:
from textblob import TextBlob
import time

l = df_sample['diagnostico']

start_time = time.time()

for x in l:
    print(f"Diagnóstico original: {x}")
    print(f"Diagnóstico corregido: {TextBlob(x).correct()}")
    print("="*25)

end_time = time.time()
execution_time = end_time - start_time
print(f"Tiempo de ejecución: {execution_time} segundos")
    

Diagnóstico original: hemorragia digestiva
Diagnóstico corregido: hemorragia digestive
Diagnóstico original: sde febril origen biliarurinario
Diagnóstico corregido: she febrile origin biliarurinario
Diagnóstico original: bacteriemia ir cr cancer pulmon
Diagnóstico corregido: bacteriemia in or cancer summon
Diagnóstico original: paralisis supranuclear progresiva
Diagnóstico corregido: paralysis supranuclear progressive
Diagnóstico original: cancer orl
Diagnóstico corregido: cancer or
Diagnóstico original: infeccion urinaria
Diagnóstico corregido: infection urinary
Diagnóstico original: ITU (infeccion tracto urinario)
Diagnóstico corregido: ITU (infection tract urinary)
Diagnóstico original: ulceras vasculares eeii
Diagnóstico corregido: ulcers vascular vein
Diagnóstico original: infeccion respiratoria
Diagnóstico corregido: infection respiratory
Diagnóstico original: cancer wpidermoide laringe
Diagnóstico corregido: cancer wpidermoide large
Diagnóstico original: cancer prostata estadio 

Diagnóstico corregido: ITU (infection tract urinary) deterioro cognitive severe
Diagnóstico original: trombosis vyugular izq
Diagnóstico corregido: thrombosis jugular in
Diagnóstico original: cancer recto
Diagnóstico corregido: cancer recto
Diagnóstico original: ITU (infeccion tracto urinario)
Diagnóstico corregido: ITU (infection tract urinary)
Diagnóstico original: demencia vascular
Diagnóstico corregido: dementia vascular
Diagnóstico original: cancer colonlnhsilicosis
Diagnóstico corregido: cancer colonlnhsilicosis
Diagnóstico original: carcinoma colon
Diagnóstico corregido: carcinoma colon
Diagnóstico original: anciana fragil
Diagnóstico corregido: ancient frail
Diagnóstico original: neo colon estadio IV
Diagnóstico corregido: neo colon studio of
Diagnóstico original: obliteracion femoro poplitea derecha
Diagnóstico corregido: obliteration femora popliteal percha
Diagnóstico original: demencia
Diagnóstico corregido: dementia
Diagnóstico original: sindrome febril
Diagnóstico corregi

Diagnóstico corregido: glioblastoma multiforme
Diagnóstico original: infeccion heridas quirurgicas
Diagnóstico corregido: infection herds quirurgicas
Diagnóstico original: abscesos hepaticos
Diagnóstico corregido: abscess hepatic
Diagnóstico original: cancer colon
Diagnóstico corregido: cancer colon
Diagnóstico original: sarcoidosis
Diagnóstico corregido: sarcoidosis
Diagnóstico original: ulcera eeii
Diagnóstico corregido: ulcer vein
Diagnóstico original: cancer ovario
Diagnóstico corregido: cancer varix
Diagnóstico original: insuficiencia renal
Diagnóstico corregido: insuficiencia renal
Diagnóstico original: anciano fragil
Diagnóstico corregido: ancient frail
Diagnóstico original: anciano fragil
Diagnóstico corregido: ancient frail
Diagnóstico original: infeccion protesis rodilla
Diagnóstico corregido: infection protests gorilla
Diagnóstico original: bacteriemia
Diagnóstico corregido: bacteriemia
Diagnóstico original: cancer prostata
Diagnóstico corregido: cancer prostate
Diagnóstico 

Diagnóstico corregido: cancer urotelial
Diagnóstico original: espondilodiscitis
Diagnóstico corregido: espondilodiscitis
Diagnóstico original: neoplasia pulmon estadio IV
Diagnóstico corregido: neoplasm summon studio of
Diagnóstico original: ITU (infeccion tracto urinario)
Diagnóstico corregido: ITU (infection tract urinary)
Diagnóstico original: cancer mama estadio IV
Diagnóstico corregido: cancer mamma studio of
Diagnóstico original: espondilodiscitis
Diagnóstico corregido: espondilodiscitis
Diagnóstico original: cancer colon
Diagnóstico corregido: cancer colon
Diagnóstico original: ela
Diagnóstico corregido: la
Diagnóstico original: ulcera vascular
Diagnóstico corregido: ulcer vascular
Diagnóstico original: infeccion urinaria
Diagnóstico corregido: infection urinary
Diagnóstico original: cancer pulmon estadio IV
Diagnóstico corregido: cancer summon studio of
Diagnóstico original: ITU (infeccion tracto urinario)
Diagnóstico corregido: ITU (infection tract urinary)
Diagnóstico origina

Diagnóstico corregido: amputation supracondileadmhtagastroparexia diabetic
Diagnóstico original: cancer pancreas estadioiv
Diagnóstico corregido: cancer pancreas estadioiv
Diagnóstico original: demencia
Diagnóstico corregido: dementia
Diagnóstico original: anciana fragil ulceras decubito
Diagnóstico corregido: ancient frail ulcers decubito
Diagnóstico original: infeccion respiratoria insuficiencia cardiaca cronica insuficiencia respiratoria
Diagnóstico corregido: infection respiratory insuficiencia cardiac chronic insuficiencia respiratory
Diagnóstico original: carcinomatosis peritoneal neoplasia digestiva baja estadio IV
Diagnóstico corregido: carcinomatous peritoneal neoplasm digestive back studio of
Diagnóstico original: infeccion respcirrosis hepatica irc hemodialisis cancer pulmon
Diagnóstico corregido: infection respcirrosis hepatic arc hemodialisis cancer summon
Diagnóstico original: neumonia
Diagnóstico corregido: pneumonia
Diagnóstico original: hepqtocarcinoma
Diagnóstico corr

In [147]:
# TextBlob no es la panacea, devuelve muchos errores y traduce al inglés además de comerse palabras
from textblob import TextBlob

def correct_spelling(df):
    for column in df:
        if df[column].dtype == 'object':  # comprueba si la columna es de tipo 'object'
            df[column] = df[column].apply(lambda x: str(TextBlob(x).correct()))

In [148]:
%%time

correct_spelling(df_sample['diagnostico'])

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ C:\Users\Pablo Villar\Desktop\CURSOS\KSchool\Máster en Data                                      │
│ Science\TFM\nuevo_entorno_kedro\lib\site-packages\IPython\core\magics\execution.py:1317 in time  │
│                                                                                                  │
│   1314 │   │   if mode=='eval':                                                                  │
│   1315 │   │   │   st = clock2()                                                                 │
│   1316 │   │   │   try:                                                                          │
│ ❱ 1317 │   │   │   │   out = eval(code, glob, local_ns)                                          │
│   1318 │   │   │   except:                                                                       │
│   1319 │   │   │   │   self.shell.showtraceback()                                                │
│   1320 │   │   │   │   return                                                                    │
│ in <module>:1                                                                                    │
│                                                                                                  │
│ in correct_spelling:6                                                                            │
│                                                                                                  │
│   3                                                                                              │
│   4 def correct_spelling(df):                                                                    │
│   5 │   for column in df:                                                                        │
│ ❱ 6 │   │   if df[column].dtype == 'object':  # comprueba si la columna es de tipo 'object'      │
│   7 │   │   │   df[column] = df[column].apply(lambda x: str(TextBlob(x).correct()))              │
│   8                                                                                              │
│                                                                                                  │
│ C:\Users\Pablo Villar\Desktop\CURSOS\KSchool\Máster en Data                                      │
│ Science\TFM\nuevo_entorno_kedro\lib\site-packages\pandas\core\series.py:981 in __getitem__       │
│                                                                                                  │
│    978 │   │   │   return self._values[key]                                                      │
│    979 │   │                                                                                     │
│    980 │   │   elif key_is_scalar:                                                               │
│ ❱  981 │   │   │   return self._get_value(key)                                                   │
│    982 │   │                                                                                     │
│    983 │   │   if is_hashable(key):                                                              │
│    984 │   │   │   # Otherwise index.get_value will raise InvalidIndexError                      │
│                                                                                                  │
│ C:\Users\Pablo Villar\Desktop\CURSOS\KSchool\Máster en Data                                      │
│ Science\TFM\nuevo_entorno_kedro\lib\site-packages\pandas\core\series.py:1089 in _get_value       │
│                                                                                                  │
│   1086 │   │   │   return self._values[label]                                                    │
│   1087 │   │                                                                                     │
│   1088 │   │   # Similar to Index.get_value, but we do not fall back to positional               │
│ ❱ 1089 │   │   loc = self.index.get_loc(label)             

In [149]:
df_sample.head()

ast_anorx s_procedencia  year dolor      motivo_alta delirium disnea  \
0        si          upal  2017    si        reingreso       no     no   
1        si     oncologia  2017    si           exitus       no     no   
2        no           mir  2017    no  fin de cuidados       no     si   
3        no     digestivo  2017    no  fin de cuidados       no     no   
4        no     urgencias  2017    si           exitus       no     si   

  h_procedencia paliativo_onc_noc  ap fiebre        medico  \
0   gil casares                si  no     no        valdes   
1       clinico                si  no     no   galego feal   
2       clinico                si  no     no  lopez renedo   
3       clinico                no  no     no  lopez renedo   
4       clinico                si  no     no  lopez renedo   

  paliativo_no_onc_noc               diagnostico sedacion  n_estancias  \
0                   si                cancer orl       no           21   
1                   no           melanoma vulvar       no           24   
2                   si       cancer broncogenico       no           14   
3                   no         cirrosis hepatica       no            1   
4                   no  neplasia mama estadio iv       no            2   

                   motivo_ing  n_visitas gds_fast  
0         control de sintomas         10       no  
1           mal control dolor          8       no  
2           control evolutivo          6       no  
3  admininistacion octreotido          1       no  
4         control de sintomas          1       no

## Conclusiones TextBlob

No nos vale para corregir ortografía en español...

# Spacy
* Textos con spacy

In [150]:
from spellchecker import SpellChecker
import spacy
from spacy.language import Language

spell = SpellChecker(language='es')  # especifica el idioma

@Language.component("spell_check")
def correct_spellings(doc):
    corrected_text = [spell.correction(word.text) if spell.correction(word.text) is not None else word.text for word in doc]
    return spacy.tokens.Doc(doc.vocab, words=corrected_text)

nlp = spacy.load('es_core_news_sm')  # carga el modelo de Spacy en español

nlp.add_pipe('spell_check', after='ner')

text = "Tus texto con errres"
doc = nlp(text)

print(doc.text)

def correct_text(text):
    doc = nlp(text)
    corrected_doc = correct_spellings(doc)
    return corrected_doc.text


Tus texto con errores 


In [152]:
%%time
df_sample['diagnostico_corregido'] = df_sample['diagnostico'].apply(correct_text)

CPU times: total: 46.1 s
Wall time: 1min 20s


In [153]:
df_sample[['diagnostico','diagnostico_corregido']]

diagnostico  \
3682                               hemorragia digestiva   
3223                   sde febril origen biliarurinario   
1851                    bacteriemia ir cr cancer pulmon   
3265                  paralisis supranuclear progresiva   
315                                          cancer orl   
1199                                 infeccion urinaria   
3094                    ITU (infeccion tracto urinario)   
1143                            ulceras vasculares eeii   
3107                             infeccion respiratoria   
3832                         cancer wpidermoide laringe   
870                          cancer prostata estadio IV   
2362  obliteracion fp IV mid hta diabetes mellitus a...   
687                                      demencia fast7   
2974                      tuberculosis pulmonar linfoma   
3079                     estesioneuroblastoma olfatorio   
1404                      neoplasia prostata estadio IV   
391                                           talasemia   
2499                             suboclusion intestinal   
1016                                       cancer recto   
829                                      cancer duodeno   
3666                                  colangiocarcinoma   
2253                                         amputacion   
3898                                     lesion cutanea   
3471                      infeccion piel partes blandas   
2546                                        cancer mama   
2248                    ITU (infeccion tracto urinario)   
841                                  infeccion protesis   
2975                         bronquiectasias infectadas   
3041                             enfermedad nieman pick   
786            ITU (infeccion tracto urinario) cirrosis   
1983                             infeccion respiratoria   
98                                  esclerosis multiple   
864                              infeccion respiratoria   
3847                                hepatopatia filiada   
2424                                           demencia   
3868                                  cirrosis hepatica   
3632                    ITU (infeccion tracto urinario)   
2440                                           neumonia   
2639                   adenocarcinima pulmon estadio IV   
2445                        neoplasia pulmon estadio IV   
2114                                cirrosis alcoholica   
2152                                         colangitis   
2383                               neo colon estadio IV   
3780                    ITU (infeccion tracto urinario)   
2197                                       cancer colon   
862                        fibrosis pulmonar idiopatica   
1544                                 neoplasia prostata   
574                                  infeccion urinaria   
837                                   cirrosis hepatica   
3628                        obliteracion femoropoplitea   
111                                    mieloma multiple   
12                                               anemia   
2073                    ITU (infeccion tracto urinario)   
1054                             cancer mama estadio IV   
1669                     insuficiencia cardiaca cronica   
433                                                 smd   
112                                        endocarditis   
670                  ituca prostata hepatopatia cronica   
3836                  colangitis aguda absceso hepatico   
1184                                     anciana fragil   
3578                       carcinoma epidermoide pulmon   
703                           demencia avanzada fast 7c   
1034                             cancer renalestadio IV   
3324                     insuficiencia cardiaca cronica   
1814                                    cancer pancreas   
1384                                            linfoma   
3562                                    hepatocarcinoma   
212                             

## Conclusiones Spacy

No nos vale para corregir ortografía en español tampoco pero es mejor que TextBlob tanto en rapidez como en resultados

# Manual con diccionario de correcciones

In [154]:
corrections = {
    'ca orl': 'cáncer oral',
    'Melanoma vulvar': 'melanoma vulvar',
    'ca broncogenico': 'cáncer broncogénico',
    
    # Añade tantas correcciones como necesites
}


In [155]:
def correct_text(text):
    words = text.split()
    corrected_words = [corrections.get(word, word) for word in words]
    corrected_text = ' '.join(corrected_words)
    return corrected_text

In [157]:
# busca todas las filas que contienen 'cancer'
df_sample['diagnostico'][df_sample['diagnostico'].str.contains('cancer',case=False)]

1851                      bacteriemia ir cr cancer pulmon
315                                            cancer orl
3832                           cancer wpidermoide laringe
870                            cancer prostata estadio IV
1016                                         cancer recto
829                                        cancer duodeno
2546                                          cancer mama
2197                                         cancer colon
1054                               cancer mama estadio IV
1034                               cancer renalestadio IV
1814                                      cancer pancreas
1571                            cancer trigono retromolar
1139                                         cancer recto
619                              cancer colonlnhsilicosis
2567                               cancer mama estadio IV
1284                                         cancer renal
2394                                      cancer hepatico
1084          

In [158]:
df_sample['diagnostico'].isna().sum()

0

In [159]:
# Solo palabras completas 'ca'
#\b es una aserción de límite de palabra en una expresión regular,
# lo que significa que 'ca' solo se encontrará si está rodeada de límites de palabra 
# (como espacios, signos de puntuación, el inicio del texto o el final del texto).


# Reemplaza los valores NaN con una cadena vacía
df_sample['diagnostico'] = df_sample['diagnostico'].fillna('')

df_sample['diagnostico'][df_sample['diagnostico'].str.contains(r'\bcancer\b', case=False, regex=True)].reset_index(drop=True)

0                       bacteriemia ir cr cancer pulmon
1                                            cancer orl
2                            cancer wpidermoide laringe
3                            cancer prostata estadio IV
4                                          cancer recto
5                                        cancer duodeno
6                                           cancer mama
7                                          cancer colon
8                                cancer mama estadio IV
9                                cancer renalestadio IV
10                                      cancer pancreas
11                            cancer trigono retromolar
12                                         cancer recto
13                             cancer colonlnhsilicosis
14                               cancer mama estadio IV
15                                         cancer renal
16                                      cancer hepatico
17                              cancer colon est

In [160]:
# Solo palabras completas 'ca'
df_sample_ca = df_sample[df_sample['diagnostico'].str.contains(r'\bcancer\b', case=False, regex=True)]


In [161]:
df_sample_ca.shape

(61, 38)

In [162]:
df_sample_ca['diagnostico']

1851                      bacteriemia ir cr cancer pulmon
315                                            cancer orl
3832                           cancer wpidermoide laringe
870                            cancer prostata estadio IV
1016                                         cancer recto
829                                        cancer duodeno
2546                                          cancer mama
2197                                         cancer colon
1054                               cancer mama estadio IV
1034                               cancer renalestadio IV
1814                                      cancer pancreas
1571                            cancer trigono retromolar
1139                                         cancer recto
619                              cancer colonlnhsilicosis
2567                               cancer mama estadio IV
1284                                         cancer renal
2394                                      cancer hepatico
1084          

In [163]:
df['diagnostico'] = df['diagnostico'].fillna('')

df['diagnostico'][df['diagnostico'].str.contains(r'\bulcera\b', case=False, regex=True)].reset_index(drop=True)

0                                           ulcera eeii
1                                 ulcera sacra grado IV
2                                  ulcera diabetica pie
3                        ulcera vascular sobreinfectada
4                                     ulcera traumatica
5                                      ulcera infectada
6                       ulcera varicosaobesidad morbida
7                                          ulcera sacra
8                                      ulcera infectada
9                                  ulcera trocanter izq
10                                        ulcera pierna
11    ulcera varicosa grave infeccion stafilo multir...
12                                     ulcera infectada
13                                     ulcera infectada
14                                     ulcera infectada
15                                      ulcera vascular
16                                      ulcera vascular
17                                      ulcera v

In [164]:
df['diagnostico'] = df['diagnostico'].fillna('')

words = ['ca', 'cncer', 'cancer', 'cáncer', 'cna']

# Convierte la lista de palabras en una expresión regular
regex = r'\b(?:{})\b'.format('|'.join(words))

# Encuentra las filas que contienen alguna de las palabras en la lista
df_cancer = df[df['diagnostico'].str.contains(regex, case=False, regex=True)]

In [165]:
df_cancer['diagnostico']

0                                              cancer orl
2                                     cancer broncogenico
9                                             cancer mama
10                                        cancer prostata
11                                        cancer prostata
14                                        cancer prostata
17                                        cancer prostata
18                                           cancer colon
19                                        cancer prostata
23                                            cancer mama
24                                        cancer pancreas
28                                            cancer timo
29                                            cancer mama
31                                        cancer prostata
38                                           cancer colon
44                                        cancer parotida
49                                cancer colon estadio IV
55            

In [166]:
df['diagnostico'] = df['diagnostico'].fillna('')

words = ['infeccion', 'inf', 'infecion', 'i', 'cna']

# Convierte la lista de palabras en una expresión regular
regex = r'\b(?:{})\b'.format('|'.join(words))

# Encuentra las filas que contienen alguna de las palabras en la lista
df_cancer = df[df['diagnostico'].str.contains(regex, case=False, regex=True)]

***limpiar los datos antes de corregir o hacer los diccionarios para clasificar los diagnósticos***

In [167]:
clean_text(df_sample)

[07/05/23 19:44:02] WARNING  C:\Users\Pablo                                                         warnings.py:109
                             Villar\AppData\Local\Temp\ipykernel_11340\2808621185.py:11:                           
                             SettingWithCopyWarning:                                                               
                             A value is trying to be set on a copy of a slice from a DataFrame.                    
                             Try using .loc[row_indexer,col_indexer] = value instead                               
                                                                                                                   
                             See the caveats in the documentation:                                                 
                             https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#                
                             returning-a-view-versus-a-copy                                                        
                               df[column] = df[column].replace('\\s+', ' ', regex=True).str.strip()                
                                                                                                                   

                    WARNING  C:\Users\Pablo                                                         warnings.py:109
                             Villar\AppData\Local\Temp\ipykernel_11340\2808621185.py:18:                           
                             SettingWithCopyWarning:                                                               
                             A value is trying to be set on a copy of a slice from a DataFrame.                    
                             Try using .loc[row_indexer,col_indexer] = value instead                               
                                                                                                                   
                             See the caveats in the documentation:                                                 
                             https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#                
                             returning-a-view-versus-a-copy                                                        
                               df[column] = df[column].str.lower()                                                 
                                                                                                                   

                    WARNING  C:\Users\Pablo                                                         warnings.py:109
                             Villar\AppData\Local\Temp\ipykernel_11340\2808621185.py:24:                           
                             SettingWithCopyWarning:                                                               
                             A value is trying to be set on a copy of a slice from a DataFrame.                    
                             Try using .loc[row_indexer,col_indexer] = value instead                               
                                                                                                                   
                             See the caveats in the documentation:                                                 
                             https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#                
                             returning-a-view-versus-a-copy                                                        
                               df[column] = df[column].apply(lambda x: unidecode.unidecode(x) if                   
                             isinstance(x, str) else x)  # quita las tildes                                        
                                                                                                                   

                    WARNING  C:\Users\Pablo                                                         warnings.py:109
                             Villar\AppData\Local\Temp\ipykernel_11340\2808621185.py:25:                           
                             SettingWithCopyWarning:                                                               
                             A value is trying to be set on a copy of a slice from a DataFrame.                    
                             Try using .loc[row_indexer,col_indexer] = value instead                               
                                                                                                                   
                             See the caveats in the documentation:                                                 
                             https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#                
                             returning-a-view-versus-a-copy                                                        
                               df[column] = df[column].str.translate(str.maketrans("", "",                         
                             string.punctuation))  # quita los signos de puntuación                                
                                                                                                                   

In [169]:
df.isna().sum().sort_values(ascending=False)

eva_ing                 2465
barthel                    1
ps_ecog                    1
ast_anorx                  0
n_visitas                  0
sedacion                   0
motivo_alta                0
medico                     0
year                       0
agudo_estable              0
otros_complicaciones       0
cronico_reag               0
trato_antibiotico          0
transfusion                0
paracentesis               0
toracocentesis             0
ayuntamiento               0
fecha_alta                 0
n_estancias                0
h_procedencia              0
otros_2                    0
fiebre                     0
ap                         0
otros                      0
diagnostico                0
motivo_ing                 0
paliativo_onc_noc          0
paliativo_no_onc_noc       0
disnea                     0
s_procedencia              0
dolor                      0
delirium                   0
otros_1                    0
p_terminal                 0
agonia        

***Elimino los valores NaN**


- Podría sacarse la media, mediana o la moda de cada columna

In [171]:
df_sample.dropna(inplace=True)

                    WARNING  C:\Users\Pablo                                                         warnings.py:109
                             Villar\AppData\Local\Temp\ipykernel_11340\2198415682.py:1:                            
                             SettingWithCopyWarning:                                                               
                             A value is trying to be set on a copy of a slice from a DataFrame                     
                                                                                                                   
                             See the caveats in the documentation:                                                 
                             https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#                
                             returning-a-view-versus-a-copy                                                        
                               df_values.dropna(inplace=True)                                                      
                                                                                                                   

<hr>

# Convertir los datos categóricos a un formato numérico:
Para convertir las variables categóricas en numéricas, puedes utilizar la función get_dummies() de pandas para realizar la codificación one-hot o la función LabelEncoder de la biblioteca scikit-learn para la codificación ordinal. Aquí tienes un ejemplo de cómo hacer la codificación one-hot:

In [174]:
df_encoded = pd.get_dummies(df_sample, columns=['dolor'])

In [1]:
df_encoded.head()

NameError: name 'df_encoded' is not defined

<hr>

#  Normalizar o estandarizar las variables numéricas:
Para normalizar o estandarizar las variables numéricas, puedes utilizar las funciones MinMaxScaler o StandardScaler de scikit-learn. Aquí tienes un ejemplo de cómo estandarizar una columna numérica:

In [176]:
from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()
df['n_visitas'] = scaler.fit_transform(df[['n_visitas']])

<hr>

# Verificar si hay errores en los datos y corregirlos:
Durante el análisis exploratorio de datos (EDA), presta atención a las distribuciones y valores atípicos. Si encuentras errores, corrige los datos según sea necesario.

<hr>

# Comprobar si hay duplicados y decidir cómo tratarlos:
Puedes utilizar la función duplicated() de pandas para encontrar registros duplicados y la función drop_duplicates() para eliminarlos. Aquí tienes un ejemplo de cómo eliminar duplicados:

In [177]:
df.drop_duplicates(inplace=True)